In [74]:
import sys
import multiprocessing
from io import StringIO
from typing import Any, Dict, Tuple


def worker_process(
    queue: multiprocessing.Queue,
    code: str,
    entry_point: str,
    params: Dict
) -> None:
    """在子进程中执行用户代码的辅助函数"""
    try:
        sys.stdout = StringIO()
        namespace = {}
        
        # 执行用户代码
        exec(code, namespace)
        
        method = eval(entry_point, namespace)

        # 执行目标方法
        result = method(**params)

        output = sys.stdout.getvalue()

        queue.put((output, result, None))

        print('output:', output)
        print('result:', result)
        
    except Exception as e:
        queue.put(("", None, str(e)))


def get_output_given_entry_point_input(
    code: str,
    entry_point: str,
    params: Dict,
) -> str:
    """改进后的安全执行函数"""

    # 创建通信队列和子进程
    ctx = multiprocessing.get_context('spawn')
    queue = ctx.Queue()
    p = ctx.Process(
        target=worker_process,
        args=(queue, code, entry_point, params)
    )
    
    try:
        p.start()
        p.join(timeout=10)  # 10秒超时
        
        if p.is_alive():
            p.terminate()
            p.join()
            return "Execution timed out"
            
        if queue.empty():
            return "No output generated"
            
        output, result, error = queue.get()
        
        if error:
            return f"Error: {error}"
            
        return str(result)
        
    except Exception as e:
        return f"System error: {str(e)}"
    

code = """def func(a: int, b: int):
    return a + b"""
entry_point = "func"
params = {'a': 2, 'b': 3}
get_output_given_entry_point_input(code, entry_point, params)

Traceback (most recent call last):
  File "<string>", line 1, in <module>
  File "/Users/xiayunhui/miniconda3/lib/python3.12/multiprocessing/spawn.py", line 122, in spawn_main
    exitcode = _main(fd, parent_sentinel)
               ^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/Users/xiayunhui/miniconda3/lib/python3.12/multiprocessing/spawn.py", line 132, in _main
    self = reduction.pickle.load(from_parent)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
AttributeError: Can't get attribute 'worker_process' on <module '__main__' (<class '_frozen_importlib.BuiltinImporter'>)>


'No output generated'

In [75]:
from eval_lcd.data import read_jsonl, write_jsonl, show_list

In [76]:
from data_process.collect_metadata import get_problem_text, get_problem_topic_tags, get_problem_question_title

In [77]:
lst = read_jsonl('data/leetcode-metadata-info2.jsonl')
show_list(lst)

List length: 3496


{'problem_id': 2591,
 'slug': 'distribute-money-to-maximum-children',
 'solutions': ['class Solution:\n    def distMoney(self, money: int, children: int) -> int:\n        if money < children:\n            return -1\n        if money > 8 * children:\n            return children - 1\n        if money == 8 * children - 4:\n            return children - 2\n        # money-8x >= children-x, x <= (money-children)/7\n        return (money - children) // 7\n',
  "class Solution:\n  def distMoney(self, money: int, children: int) -> int:\n    # Everyone must receive at least 1 dollar.\n    money -= children\n    if money < 0:\n      return -1\n\n    count7 = money // 7\n    remaining = money % 7\n\n    # Distribute 8 dollars to every child.\n    if count7 == children and remaining == 0:\n      return count7\n\n    # Need to move 1 dollar from the last child with 4 dollars to one of other\n    # children. That's why we need to substract 1.\n    if count7 == children - 1 and remaining == 3:\n     

In [78]:
from tqdm import tqdm

for item in tqdm(lst):
    assert item['problem_id'] and item['slug']
    # if 'lang_code' not in item or 'question_title_en' not in item or not item['lang_code'] or not item['question_title_en']:
    item['text'] = get_problem_text(slug=item['slug'])
show_list(lst)

  0%|          | 2/3496 [00:02<1:10:20,  1.21s/it]


KeyboardInterrupt: 

In [5]:
write_jsonl('data/leetcode-metadata-info3.jsonl', lst)

In [6]:
from data_process.collect_metadata import get_problem_lang_code, get_problem_question_title

lst = read_jsonl('data/leetcode-metadata-info3.jsonl')
show_list(lst)

List length: 3496


{'problem_id': 2591,
 'slug': 'distribute-money-to-maximum-children',
 'solutions': ['class Solution:\n    def distMoney(self, money: int, children: int) -> int:\n        if money < children:\n            return -1\n        if money > 8 * children:\n            return children - 1\n        if money == 8 * children - 4:\n            return children - 2\n        # money-8x >= children-x, x <= (money-children)/7\n        return (money - children) // 7\n',
  "class Solution:\n  def distMoney(self, money: int, children: int) -> int:\n    # Everyone must receive at least 1 dollar.\n    money -= children\n    if money < 0:\n      return -1\n\n    count7 = money // 7\n    remaining = money % 7\n\n    # Distribute 8 dollars to every child.\n    if count7 == children and remaining == 0:\n      return count7\n\n    # Need to move 1 dollar from the last child with 4 dollars to one of other\n    # children. That's why we need to substract 1.\n    if count7 == children - 1 and remaining == 3:\n     

In [17]:
write_jsonl('data/leetcode-metadata-info4.jsonl', lst)

In [6]:
from eval_lcd.data import read_jsonl, write_jsonl, show_list
from data_process.collect_metadata import get_problem_lang_code, html_to_text, trans_format

In [ ]:
lst = read_jsonl('data/leetcode-metadata-info4.jsonl')
show_list(lst)

List length: 3496


{'problem_id': 2591,
 'slug': 'distribute-money-to-maximum-children',
 'solutions': ['class Solution:\n    def distMoney(self, money: int, children: int) -> int:\n        if money < children:\n            return -1\n        if money > 8 * children:\n            return children - 1\n        if money == 8 * children - 4:\n            return children - 2\n        # money-8x >= children-x, x <= (money-children)/7\n        return (money - children) // 7\n',
  "class Solution:\n  def distMoney(self, money: int, children: int) -> int:\n    # Everyone must receive at least 1 dollar.\n    money -= children\n    if money < 0:\n      return -1\n\n    count7 = money // 7\n    remaining = money % 7\n\n    # Distribute 8 dollars to every child.\n    if count7 == children and remaining == 0:\n      return count7\n\n    # Need to move 1 dollar from the last child with 4 dollars to one of other\n    # children. That's why we need to substract 1.\n    if count7 == children - 1 and remaining == 3:\n     

In [7]:
import re

def get_problem_lang_code(text: str) -> str:
    if r'","lang":"Python3","langSlug":"python3"' in text:
        pattern = r'.*"code":"(.*?)","lang":"Python3","langSlug":"python3"'
        match = re.search(pattern, text, re.DOTALL)
        if match:
            m = match.group(1)
            return html_to_text(trans_format(m))
    return ''

In [ ]:
from tqdm import tqdm

for item in tqdm(lst):
    item['new_lang_code'] = get_problem_lang_code(item['text'])
show_list(lst)

100%|██████████| 3496/3496 [00:20<00:00, 167.51it/s]

List length: 3496


{'problem_id': 2591,
 'slug': 'distribute-money-to-maximum-children',
 'solutions': ['class Solution:\n    def distMoney(self, money: int, children: int) -> int:\n        if money < children:\n            return -1\n        if money > 8 * children:\n            return children - 1\n        if money == 8 * children - 4:\n            return children - 2\n        # money-8x >= children-x, x <= (money-children)/7\n        return (money - children) // 7\n',
  "class Solution:\n  def distMoney(self, money: int, children: int) -> int:\n    # Everyone must receive at least 1 dollar.\n    money -= children\n    if money < 0:\n      return -1\n\n    count7 = money // 7\n    remaining = money % 7\n\n    # Distribute 8 dollars to every child.\n    if count7 == children and remaining == 0:\n      return count7\n\n    # Need to move 1 dollar from the last child with 4 dollars to one of other\n    # children. That's why we need to substract 1.\n    if count7 == children - 1 and remaining == 3:\n     

In [ ]:
write_jsonl('data/leetcode-metadata-info5.jsonl', lst)

In [18]:
for i, item in enumerate(lst[: 500]):
    assert item['new_question_title']
    print(i)
    print(item['new_question_title'], '\n\n\n')

0
You are given an integer money denoting the amount of money (in dollars) that you have and another integer children denoting the number of children that you must distribute the money to.
You have to distribute the money according to the following rules:

All money must be distributed.
Everyone must receive at least 1 dollar.
Nobody receives 4 dollars.

Return the maximum number of children who may receive exactly 8 dollars if you distribute the money according to the aforementioned rules. If there is no way to distribute the money, return -1.
 
Example 1:

Input: money = 20, children = 3
Output: 1
Explanation: 
The maximum number of children with 8 dollars will be 1. One of the ways to distribute the money is:
- 8 dollars to the first child.
- 9 dollars to the second child. 
- 3 dollars to the third child.
It can be proven that no distribution exists such that number of children getting 8 dollars is greater than 1.

Example 2:

Input: money = 16, children = 2
Output: 2
Explanation: E

In [30]:
import requests
import json

def get_leetcode_problems() -> list:
    """
    Fetch the complete problem list from LeetCode's API.
    
    Returns:
        dict: A dictionary containing all LeetCode problems and their metadata
    """
    url = "https://leetcode.com/api/problems/all/"
    response = requests.get(url)
    response.raise_for_status()  # Raise an exception for bad status codes
    info = response.json()
    
    result = []
    for item in info['stat_status_pairs']:
        if item['difficulty']['level'] == 1:
            difficulty = 'Easy'
        elif item['difficulty']['level'] == 2:
            difficulty = 'Medium'
        else:
            assert item['difficulty']['level'] == 3
            difficulty = 'Hard'
        result.append({
            'slug': item['stat']['question__title_slug'], 
            'difficulty': difficulty})
    return result
    
lst = get_leetcode_problems()

In [31]:
lst[0]

{'slug': 'analyze-subscription-conversion', 'difficulty': 'Medium'}

In [32]:
lst = read_jsonl('data/leetcode-basic-metadata-2025-03-30-12-40-09.jsonl')
show_list(lst)

List length: 3501


{'slug': 'two-sum',
 'difficulty': 'Easy',
 'problem_id': 1,
 'solutions': ['class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n        d = {}\n        for i, x in enumerate(nums):\n            if (y := target - x) in d:\n                return [d[y], i]\n            d[x] = i\n',
  'class Solution:\n  def twoSum(self, nums: list[int], target: int) -> list[int]:\n    numToIndex = {}\n\n    for i, num in enumerate(nums):\n      if target - num in numToIndex:\n        return numToIndex[target - num], i\n      numToIndex[num] = i\n']}

In [33]:
lst[-1]

{'slug': 'maximize-active-section-with-trade-ii',
 'difficulty': 'Hard',
 'problem_id': 3501,
 'solutions': []}

In [ ]:
from data_process.collect_metadata import get_leetcode_problems

In [2]:
lst = get_leetcode_problems()

In [ ]:
from eval_lcd.data import *

In [5]:
lst = read_jsonl('data/leetcode-basic-metadata-2025-03-30-13-40-21.jsonl')
show_list(lst)

List length: 3505


{'slug': 'two-sum',
 'difficulty': 'Easy',
 'problem_id': 1,
 'solutions': ['class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n        d = {}\n        for i, x in enumerate(nums):\n            if (y := target - x) in d:\n                return [d[y], i]\n            d[x] = i\n',
  'class Solution:\n  def twoSum(self, nums: list[int], target: int) -> list[int]:\n    numToIndex = {}\n\n    for i, num in enumerate(nums):\n      if target - num in numToIndex:\n        return numToIndex[target - num], i\n      numToIndex[num] = i\n']}

In [ ]:
l = read_jsonl('data/leetcode-metadata-info5.jsonl')
show_list(l)

List length: 3496


{'problem_id': 2591,
 'slug': 'distribute-money-to-maximum-children',
 'solutions': ['class Solution:\n    def distMoney(self, money: int, children: int) -> int:\n        if money < children:\n            return -1\n        if money > 8 * children:\n            return children - 1\n        if money == 8 * children - 4:\n            return children - 2\n        # money-8x >= children-x, x <= (money-children)/7\n        return (money - children) // 7\n',
  "class Solution:\n  def distMoney(self, money: int, children: int) -> int:\n    # Everyone must receive at least 1 dollar.\n    money -= children\n    if money < 0:\n      return -1\n\n    count7 = money // 7\n    remaining = money % 7\n\n    # Distribute 8 dollars to every child.\n    if count7 == children and remaining == 0:\n      return count7\n\n    # Need to move 1 dollar from the last child with 4 dollars to one of other\n    # children. That's why we need to substract 1.\n    if count7 == children - 1 and remaining == 3:\n     

In [24]:
cnt = 0
for item in l:
    if 'lang_code' in item and 'new_lang_code' in item:
        if item['lang_code'] == item['new_lang_code']:
            cnt += 1
cnt

2646

In [7]:
slug2item = {item['slug']: item for item in l}
len(slug2item)

3496

In [8]:
from data_process.collect_metadata import get_problem_text, get_problem_topic_tags, get_problem_question_title, get_problem_lang_code

In [ ]:
from tqdm import tqdm

for item in tqdm(lst):
    slug = item['slug']
    if slug in slug2item:
        x = slug2item[slug]
        item['text'] = x['text']
        item['topic_tags'] = x['topic_tags']
        item['question_title'] = x['new_question_title']
        item['lang_code'] = x['new_lang_code']
    else:
        text = get_problem_text(slug)
        item['text'] = text
        item['topic_tags'] = get_problem_topic_tags(text)
        item['question_title'] = get_problem_question_title(text)
        item['lang_code'] = get_problem_lang_code(text)
show_list(lst)

100%|██████████| 3505/3505 [00:08<00:00, 399.72it/s] 

List length: 3505


{'slug': 'two-sum',
 'difficulty': 'Easy',
 'problem_id': 1,
 'solutions': ['class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n        d = {}\n        for i, x in enumerate(nums):\n            if (y := target - x) in d:\n                return [d[y], i]\n            d[x] = i\n',
  'class Solution:\n  def twoSum(self, nums: list[int], target: int) -> list[int]:\n    numToIndex = {}\n\n    for i, num in enumerate(nums):\n      if target - num in numToIndex:\n        return numToIndex[target - num], i\n      numToIndex[num] = i\n'],
 'text': '<!DOCTYPE html>\n<html lang="zh"><head><meta charset="utf-8" data-next-head=""/><meta content="width=device-width" data-next-head="" name="viewport"/><meta content="summary_large_image" data-next-head="" name="twitter:card"/><meta content="@LeetCode" data-next-head="" name="twitter:site"/><meta content="https://static.leetcode-cn.com/cn-legacy-assets/images/LeetCode_Sharing.png" data-next-head="" property="og:image"/>

In [19]:
write_jsonl('data/leetcode-metadata-2025-03-30.jsonl', lst)

In [96]:
lst = read_jsonl('data/leetcode-metadata-2025-03-30.jsonl')
show_list(lst)

List length: 3505


{'slug': 'two-sum',
 'difficulty': 'Easy',
 'problem_id': 1,
 'solutions': ['class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n        d = {}\n        for i, x in enumerate(nums):\n            if (y := target - x) in d:\n                return [d[y], i]\n            d[x] = i\n',
  'class Solution:\n  def twoSum(self, nums: list[int], target: int) -> list[int]:\n    numToIndex = {}\n\n    for i, num in enumerate(nums):\n      if target - num in numToIndex:\n        return numToIndex[target - num], i\n      numToIndex[num] = i\n'],
 'text': '<!DOCTYPE html>\n<html lang="zh"><head><meta charset="utf-8" data-next-head=""/><meta content="width=device-width" data-next-head="" name="viewport"/><meta content="summary_large_image" data-next-head="" name="twitter:card"/><meta content="@LeetCode" data-next-head="" name="twitter:site"/><meta content="https://static.leetcode-cn.com/cn-legacy-assets/images/LeetCode_Sharing.png" data-next-head="" property="og:image"/>

In [97]:
sum(1 for item in lst if item['lang_code'])

3115

In [98]:
l = [item for item in lst if item['lang_code']]
show_list(l)

List length: 3115


{'slug': 'two-sum',
 'difficulty': 'Easy',
 'problem_id': 1,
 'solutions': ['class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n        d = {}\n        for i, x in enumerate(nums):\n            if (y := target - x) in d:\n                return [d[y], i]\n            d[x] = i\n',
  'class Solution:\n  def twoSum(self, nums: list[int], target: int) -> list[int]:\n    numToIndex = {}\n\n    for i, num in enumerate(nums):\n      if target - num in numToIndex:\n        return numToIndex[target - num], i\n      numToIndex[num] = i\n'],
 'text': '<!DOCTYPE html>\n<html lang="zh"><head><meta charset="utf-8" data-next-head=""/><meta content="width=device-width" data-next-head="" name="viewport"/><meta content="summary_large_image" data-next-head="" name="twitter:card"/><meta content="@LeetCode" data-next-head="" name="twitter:site"/><meta content="https://static.leetcode-cn.com/cn-legacy-assets/images/LeetCode_Sharing.png" data-next-head="" property="og:image"/>

In [99]:
l1 = [item for item in l if 'TreeNode' not in item['lang_code'] and 'ListNode' not in item['lang_code']]
l2 = [item for item in l if 'TreeNode' in item['lang_code']]
l3 = [item for item in l if 'ListNode' in item['lang_code']]
show_list(l1)
show_list(l2)
show_list(l3)

List length: 2912
List length: 153
List length: 52


{'slug': 'add-two-numbers',
 'difficulty': 'Medium',
 'problem_id': 2,
 'solutions': ['# Definition for singly-linked list.\n# class ListNode:\n#     def __init__(self, val=0, next=None):\n#         self.val = val\n#         self.next = next\nclass Solution:\n    def addTwoNumbers(\n        self, l1: Optional[ListNode], l2: Optional[ListNode]\n    ) -> Optional[ListNode]:\n        dummy = ListNode()\n        carry, curr = 0, dummy\n        while l1 or l2 or carry:\n            s = (l1.val if l1 else 0) + (l2.val if l2 else 0) + carry\n            carry, val = divmod(s, 10)\n            curr.next = ListNode(val)\n            curr = curr.next\n            l1 = l1.next if l1 else None\n            l2 = l2.next if l2 else None\n        return dummy.next\n',
  'class Solution:\n  def addTwoNumbers(self, l1: ListNode, l2: ListNode) -> ListNode:\n    dummy = ListNode(0)\n    curr = dummy\n    carry = 0\n\n    while carry or l1 or l2:\n      if l1:\n        carry += l1.val\n        l1 = l1.nex

In [105]:
import random

x = random.choice(l1)
print(x['question_title'] + '\n\n' + x['lang_code'])

In a project, you have a list of required skills req_skills, and a list of people. The ith person people[i] contains a list of skills that the person has.
Consider a sufficient team: a set of people such that for every required skill in req_skills, there is at least one person in the team who has that skill. We can represent these teams by the index of each person.

For example, team = [0, 1, 3] represents the people with skills people[0], people[1], and people[3].

Return any sufficient team of the smallest possible size, represented by the index of each person. You may return the answer in any order.
It is guaranteed an answer exists.
 
Example 1:
Input: req_skills = ["java","nodejs","reactjs"], people = [["java"],["nodejs"],["nodejs","reactjs"]]
Output: [0,2]
Example 2:
Input: req_skills = ["algorithms","math","java","reactjs","csharp","aws"], people = [["algorithms","math","java"],["algorithms","math","reactjs"],["java","csharp","aws"],["reactjs","csharp"],["csharp","math"],["aws",

In [106]:
x['inputs'] = ['req_skills = ["java","nodejs","reactjs"], people = [["java"],["nodejs"],["nodejs","reactjs"]]', 'nums = [1,3,2,6,4,2], k = 3, dist = 3', 'req_skills = ["algorithms","math","java","reactjs","csharp","aws"], people = [["algorithms","math","java"],["algorithms","math","reactjs"],["java","csharp","aws"],["reactjs","csharp"],["csharp","math"],["aws","java"]]']

In [ ]:
from typing import List

def _gen_json_inputs(inputs: List[str]):
    return "```json\n" + json.dumps(inputs, ensure_ascii=False, indent=4) + "\n```\n\n"

In [51]:
r = [item for item in l if 'inputs' in item]
show_list(r)

List length: 5


{'slug': 'add-two-numbers',
 'difficulty': 'Medium',
 'problem_id': 2,
 'solutions': ['# Definition for singly-linked list.\n# class ListNode:\n#     def __init__(self, val=0, next=None):\n#         self.val = val\n#         self.next = next\nclass Solution:\n    def addTwoNumbers(\n        self, l1: Optional[ListNode], l2: Optional[ListNode]\n    ) -> Optional[ListNode]:\n        dummy = ListNode()\n        carry, curr = 0, dummy\n        while l1 or l2 or carry:\n            s = (l1.val if l1 else 0) + (l2.val if l2 else 0) + carry\n            carry, val = divmod(s, 10)\n            curr.next = ListNode(val)\n            curr = curr.next\n            l1 = l1.next if l1 else None\n            l2 = l2.next if l2 else None\n        return dummy.next\n',
  'class Solution:\n  def addTwoNumbers(self, l1: ListNode, l2: ListNode) -> ListNode:\n    dummy = ListNode(0)\n    curr = dummy\n    carry = 0\n\n    while carry or l1 or l2:\n      if l1:\n        carry += l1.val\n        l1 = l1.nex

In [61]:
write_jsonl('data/leetcode-metadata-2025-03-30-python-sample-inputs.jsonl', l)

In [95]:
lst = read_jsonl('data/leetcode-metadata-2025-03-30-python-sample-inputs.jsonl')
show_list(lst)

List length: 3115


{'slug': 'two-sum',
 'difficulty': 'Easy',
 'problem_id': 1,
 'solutions': ['class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n        d = {}\n        for i, x in enumerate(nums):\n            if (y := target - x) in d:\n                return [d[y], i]\n            d[x] = i\n',
  'class Solution:\n  def twoSum(self, nums: list[int], target: int) -> list[int]:\n    numToIndex = {}\n\n    for i, num in enumerate(nums):\n      if target - num in numToIndex:\n        return numToIndex[target - num], i\n      numToIndex[num] = i\n'],
 'text': '<!DOCTYPE html>\n<html lang="zh"><head><meta charset="utf-8" data-next-head=""/><meta content="width=device-width" data-next-head="" name="viewport"/><meta content="summary_large_image" data-next-head="" name="twitter:card"/><meta content="@LeetCode" data-next-head="" name="twitter:site"/><meta content="https://static.leetcode-cn.com/cn-legacy-assets/images/LeetCode_Sharing.png" data-next-head="" property="og:image"/>

In [63]:
l1 = [item for item in lst if 'TreeNode' not in item['lang_code'] and 'ListNode' not in item['lang_code'] and 'inputs' in item]
l2 = [item for item in lst if 'TreeNode' in item['lang_code'] and 'inputs' in item]
l3 = [item for item in lst if 'ListNode' in item['lang_code'] and 'inputs' in item]
show_list(l1)
show_list(l2)
show_list(l3)

List length: 2
List length: 2
List length: 1


{'slug': 'add-two-numbers',
 'difficulty': 'Medium',
 'problem_id': 2,
 'solutions': ['# Definition for singly-linked list.\n# class ListNode:\n#     def __init__(self, val=0, next=None):\n#         self.val = val\n#         self.next = next\nclass Solution:\n    def addTwoNumbers(\n        self, l1: Optional[ListNode], l2: Optional[ListNode]\n    ) -> Optional[ListNode]:\n        dummy = ListNode()\n        carry, curr = 0, dummy\n        while l1 or l2 or carry:\n            s = (l1.val if l1 else 0) + (l2.val if l2 else 0) + carry\n            carry, val = divmod(s, 10)\n            curr.next = ListNode(val)\n            curr = curr.next\n            l1 = l1.next if l1 else None\n            l2 = l2.next if l2 else None\n        return dummy.next\n',
  'class Solution:\n  def addTwoNumbers(self, l1: ListNode, l2: ListNode) -> ListNode:\n    dummy = ListNode(0)\n    curr = dummy\n    carry = 0\n\n    while carry or l1 or l2:\n      if l1:\n        carry += l1.val\n        l1 = l1.nex

In [107]:
from data_process.prompts import prompt_gen_inputs_using_example

In [82]:
for item in lst:
    if 'TreeNode' in item['lang_code']:
        x = random.choice(l2)
    elif 'ListNode' in item['lang_code']:
        x = random.choice(l3)
    else:
        x = random.choice(l1)
    example_desc = x['question_title'] + '\nStarter code:\n' + x['lang_code']
    example_inputs = x['inputs']
    problem_desc = item['question_title'] + '\nStarter code:\n' + item['lang_code']
    item['gen_input_query'] = prompt_gen_inputs_using_example(problem_desc=problem_desc, example_desc=example_desc, example_inputs=example_inputs)
    item['query'] = item['gen_input_query']
show_list(lst)

List length: 3115


{'slug': 'two-sum',
 'difficulty': 'Easy',
 'problem_id': 1,
 'solutions': ['class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n        d = {}\n        for i, x in enumerate(nums):\n            if (y := target - x) in d:\n                return [d[y], i]\n            d[x] = i\n',
  'class Solution:\n  def twoSum(self, nums: list[int], target: int) -> list[int]:\n    numToIndex = {}\n\n    for i, num in enumerate(nums):\n      if target - num in numToIndex:\n        return numToIndex[target - num], i\n      numToIndex[num] = i\n'],
 'text': '<!DOCTYPE html>\n<html lang="zh"><head><meta charset="utf-8" data-next-head=""/><meta content="width=device-width" data-next-head="" name="viewport"/><meta content="summary_large_image" data-next-head="" name="twitter:card"/><meta content="@LeetCode" data-next-head="" name="twitter:site"/><meta content="https://static.leetcode-cn.com/cn-legacy-assets/images/LeetCode_Sharing.png" data-next-head="" property="og:image"/>

In [83]:
for item in lst:
    del item['text']
show_list(lst)

List length: 3115


{'slug': 'two-sum',
 'difficulty': 'Easy',
 'problem_id': 1,
 'solutions': ['class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n        d = {}\n        for i, x in enumerate(nums):\n            if (y := target - x) in d:\n                return [d[y], i]\n            d[x] = i\n',
  'class Solution:\n  def twoSum(self, nums: list[int], target: int) -> list[int]:\n    numToIndex = {}\n\n    for i, num in enumerate(nums):\n      if target - num in numToIndex:\n        return numToIndex[target - num], i\n      numToIndex[num] = i\n'],
 'topic_tags': ['Array', 'Hash Table'],
 'question_title': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because 

In [84]:
write_jsonl('data/leetcode-metadata-2025-03-30-python-gen-inputs-5-times.jsonl', [item for _ in range(5) for item in lst])

In [89]:
lst1 = read_jsonl('data/leetcode-metadata-2025-03-30-python-gen-inputs-5-times.jsonl')
lst2 = read_jsonl('vllm_predict-leetcode-0330-gen-inputs.jsonl')
show_list(lst1)
show_list(lst2)

List length: 15575
List length: 15575


{'query': 'You are an expert Python programmer. You will be given a question (including a problem specification and starter code). Your task is to generate inputs that are consistent with the problem specification and starter code. An example will be provided for illustration.\n\n**** Example ****\n\n#### Question:\nYou are given an integer eventTime denoting the duration of an event. You are also given two integer arrays startTime and endTime, each of length n.\nThese represent the start and end times of n non-overlapping meetings that occur during the event between time t = 0 and time t = eventTime, where the ith meeting occurs during the time [startTime[i], endTime[i]].\nYou can reschedule at most one meeting by moving its start time while maintaining the same duration, such that the meetings remain non-overlapping, to maximize the longest continuous period of free time during the event.\nReturn the maximum amount of free time possible after rearranging the meetings.\nNote that the 

In [90]:
from utils import extract_code_blocks
from collections import defaultdict

id2inputs = defaultdict(set)
for a, b in zip(lst1, lst2):
    assert a['query'] == b['query']
    code_blocks = extract_code_blocks(b['output'], 'json')
    try:
        tmp = json.loads(code_blocks[0])
        for text in tmp:
            id2inputs[a['slug']].add(text)
    except:
        continue
len(id2inputs)

3114

In [93]:
s = set()
for k, v in id2inputs.items():
    if not v:
        s.add(k)
len(s)

105

In [94]:
for a, b in zip(lst1, lst2):
    if a['slug'] in s:
        print(b['output'], '\n\n\n')

```json
[
    {"l1": [2,4,3], "l2": [5,6,4]},
    {"l1": [0], "l2": [0]},
    {"l1": [9,9,9,9,9,9,9], "l2": [9,9,9,9]}
]
``` 



```json
[
    "board = [["5","3",".",".","7",".",".",".","."],["6",".",".","1","9","5",".",".","."],[".","9","8",".",".",".",".","6","."],["8",".",".",".","6",".",".",".","3"],["4",".",".","8",".","3",".",".","1"],["7",".",".",".","2",".",".",".","6"],[".","6",".",".",".",".","2","8","."],[".",".",".","4","1","9",".",".","5"],[".",".",".",".","8",".",".","7","9"]]"
]
``` 



```json
[
    {"root": [5,4,8,11,null,13,4,7,2,null,null,5,1], "targetSum": 22},
    {"root": [1,2,3], "targetSum": 5},
    {"root": [1,2], "targetSum": 0},
    {"root": [], "targetSum": 0},
    {"root": [10,5,-3,3,2,null,11,3,-2,null,1], "targetSum": 8}
]
``` 



```json
[
    {"head": [[7,null],[13,0],[11,4],[10,2],[1,0]]},
    {"head": [[1,1],[2,1]]},
    {"head": [[3,null],[3,0],[3,null]]},
    {"head": []}
]
``` 



```json
[
    ["MinStack", "push", "push", "push", "getMin", "pop", 

In [85]:
for k, v in id2inputs.items():
    assert v

AssertionError: 

In [68]:
result = []
other = []
for item in lst1[: 3115]:
    if item['slug'] not in id2inputs:
        other.append(item)
    else:
        item['inputs'] = list(id2inputs[item['slug']])
        result.append(item)
show_list(result)

List length: 3114


{'slug': 'two-sum',
 'difficulty': 'Easy',
 'problem_id': 1,
 'solutions': ['class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n        d = {}\n        for i, x in enumerate(nums):\n            if (y := target - x) in d:\n                return [d[y], i]\n            d[x] = i\n',
  'class Solution:\n  def twoSum(self, nums: list[int], target: int) -> list[int]:\n    numToIndex = {}\n\n    for i, num in enumerate(nums):\n      if target - num in numToIndex:\n        return numToIndex[target - num], i\n      numToIndex[num] = i\n'],
 'topic_tags': ['Array', 'Hash Table'],
 'question_title': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because 

In [69]:
write_jsonl('data/leetcode-metadata-2025-03-30-python-inputs.jsonl', result)

In [74]:
lst1 = read_jsonl('data/leetcode-metadata-2025-03-30-python-gen-complex-inputs-10-times.jsonl')
lst2 = read_jsonl('vllm_predict-leetcode-0330-gen-complex-input.jsonl')
show_list(lst1)
show_list(lst2)

List length: 31140
List length: 31140


{'query': 'You are an expert Python programmer. You will be given a question (including a problem specification and starter code) along with a few sample inputs. Your task is to generate additional inputs that are consistent with the question and the provided sample inputs.\n\n#### Question:\nGiven an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come 

In [79]:
from utils import extract_code_blocks
from collections import defaultdict

id2complex = defaultdict(set)
for a, b in zip(lst1, lst2):
    assert a['query'] == b['query']
    code_blocks = extract_code_blocks(b['output'], 'json')
    try:
        tmp = json.loads(code_blocks[0])
        for text in tmp:
            id2complex[a['slug']].add(text)
    except:
        continue
len(id2complex)

3102

In [83]:
for item in lst1[: 3114]:
    inputs = id2inputs[item['slug']]
    assert inputs
    complex = id2complex.get(item['slug'], [])
    for s in complex:
        if s not in inputs:
            inputs.add(s)
    item['inputs'] = list(inputs)
show_list(lst1[: 3114])

AssertionError: 

In [82]:
for item in lst1[: 3114]:
    assert item['inputs']

AssertionError: 

In [110]:
write_jsonl('data/leetcode-metadata-2025-03-30-python-inputs-complex.jsonl', lst1[: 3114])

In [109]:
x = random.choice(other)
x

{'slug': 'minimum-number-of-food-buckets-to-feed-the-hamsters',
 'difficulty': 'Medium',
 'problem_id': 2086,
 'solutions': ["class Solution:\n    def minimumBuckets(self, street: str) -> int:\n        ans = 0\n        i, n = 0, len(street)\n        while i < n:\n            if street[i] == 'H':\n                if i + 1 < n and street[i + 1] == '.':\n                    i += 2\n                    ans += 1\n                elif i and street[i - 1] == '.':\n                    ans += 1\n                else:\n                    return -1\n            i += 1\n        return ans\n",
  "class Solution:\n  def minimumBuckets(self, street: str) -> int:\n    A = list(street)\n\n    for i, c in enumerate(A):\n      if c == 'H':\n        if i > 0 and A[i - 1] == 'B':\n          continue\n        if i + 1 < len(A) and A[i + 1] == '.':\n          # Always prefer place a bucket in (i + 1) because it enhances the\n          # possibility to collect the upcoming houses.\n          A[i + 1] = 'B'\n

In [96]:
write_jsonl('data/leetcode-metadata-2025-03-30-python-inputs.jsonl', result)
write_jsonl('data/leetcode-metadata-2025-03-30-python-no-inputs.jsonl', other)

In [97]:
lst = read_jsonl('data/leetcode-metadata-2025-03-30-python-inputs.jsonl')
show_list(lst)

List length: 3114


{'slug': 'two-sum',
 'difficulty': 'Easy',
 'problem_id': 1,
 'solutions': ['class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n        d = {}\n        for i, x in enumerate(nums):\n            if (y := target - x) in d:\n                return [d[y], i]\n            d[x] = i\n',
  'class Solution:\n  def twoSum(self, nums: list[int], target: int) -> list[int]:\n    numToIndex = {}\n\n    for i, num in enumerate(nums):\n      if target - num in numToIndex:\n        return numToIndex[target - num], i\n      numToIndex[num] = i\n'],
 'topic_tags': ['Array', 'Hash Table'],
 'question_title': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because 

In [101]:
from data_process.prompts import prompt_gen_inputs

result = []
for _ in range(10):
    for item in lst:
        problem_desc = problem_desc = item['question_title'] + '\nStarter code:\n' + item['lang_code']
        sample_inputs = random.sample(item['inputs'], min(len(item['inputs']), 3))
        item['gen_complex_input_query'] = prompt_gen_inputs(problem_desc=problem_desc, sample_inputs=sample_inputs)
        item['query'] = item['gen_complex_input_query']
        result.append(item)
show_list(result)

List length: 31140


{'slug': 'two-sum',
 'difficulty': 'Easy',
 'problem_id': 1,
 'solutions': ['class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n        d = {}\n        for i, x in enumerate(nums):\n            if (y := target - x) in d:\n                return [d[y], i]\n            d[x] = i\n',
  'class Solution:\n  def twoSum(self, nums: list[int], target: int) -> list[int]:\n    numToIndex = {}\n\n    for i, num in enumerate(nums):\n      if target - num in numToIndex:\n        return numToIndex[target - num], i\n      numToIndex[num] = i\n'],
 'topic_tags': ['Array', 'Hash Table'],
 'question_title': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because 

In [104]:
x = random.choice(result)
print(x['query'])

You are an expert Python programmer. You will be given a question (including a problem specification and starter code) along with a few sample inputs. Your task is to generate additional inputs that are consistent with the question and the provided sample inputs.

#### Question:
You are given an m x n binary matrix grid.
A row or column is considered palindromic if its values read the same forward and backward.
You can flip any number of cells in grid from 0 to 1, or from 1 to 0.
Return the minimum number of cells that need to be flipped to make all rows and columns palindromic, and the total number of 1's in grid divisible by 4.
 
Example 1:

Input: grid = [[1,0,0],[0,1,0],[0,0,1]]
Output: 3
Explanation:


Example 2:

Input: grid = [[0,1],[0,1],[0,0]]
Output: 2
Explanation:


Example 3:

Input: grid = [[1],[1]]
Output: 2
Explanation:


 
Constraints:

m == grid.length
n == grid[i].length
1 <= m * n <= 2 * 105
0 <= grid[i][j] <= 1


Starter code:
class Solution:
    def minFlips(self, 

In [103]:
write_jsonl('data/leetcode-metadata-2025-03-30-python-gen-complex-inputs-10-times.jsonl', result)

In [113]:
l = read_jsonl('data/leetcode-0312-single-2924-good-cases.jsonl')
show_list(l)
prompt = l[0]['prompt']

List length: 2794


In [115]:
lst = read_jsonl('data/leetcode-metadata-2025-03-30-python-inputs-complex.jsonl')
show_list(lst)
lst[-1]

List length: 3114


{'slug': 'minimum-operations-to-make-elements-within-k-subarrays-equal',
 'difficulty': 'Hard',
 'problem_id': 3505,
 'solutions': [],
 'topic_tags': [],
 'question_title': 'You are given an integer array nums and two integers, x and k. You can perform the following operation any number of times (including zero):\n\nIncrease or decrease any element of nums by 1.\n\nReturn the minimum number of operations needed to have at least k non-overlapping subarrays of size exactly x in nums, where all elements within each subarray are equal.\n\xa0\nExample 1:\n\nInput: nums = [5,-2,1,3,7,3,6,4,-1], x = 3, k = 2\nOutput: 8\nExplanation:\n\nUse 3 operations to add 3 to nums[1] and use 2 operations to subtract 2 from nums[3]. The resulting array is [5, 1, 1, 1, 7, 3, 6, 4, -1].\nUse 1 operation to add 1 to nums[5] and use 2 operations to subtract 2 from nums[6]. The resulting array is [5, 1, 1, 1, 7, 4, 4, 4, -1].\nNow, all elements within each subarray [1, 1, 1] (from indices 1 to 3) and [4, 4, 4]

In [118]:
from data_process.utils import parse_classes_and_methods

result = []
for item in tqdm(lst):
    dct = parse_classes_and_methods(item['lang_code'])
    if len(dct) == 1:
        entry_point = ""
        for k, v in dct.items():
            if len(v) == 1:
                entry_point = f"{k}().{v[0]}"
        if entry_point:
            item['task_id'] = item['slug']
            item['prompt'] = prompt
            item['completion'] = item['solutions'][0] if item['solutions'] else ''
            item['entry_point'] = entry_point
            item['test'] = ''
            result.append(item)
show_list(result)
write_jsonl('data/leetcode-metadata-2025-03-30-single.jsonl', result)

100%|██████████| 3114/3114 [00:00<00:00, 247537.39it/s]

List length: 2945


In [119]:
lst = read_jsonl('data/leetcode-metadata-2025-03-30-single.jsonl')
show_list(lst)

List length: 2945


{'slug': 'two-sum',
 'difficulty': 'Easy',
 'problem_id': 1,
 'solutions': ['class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n        d = {}\n        for i, x in enumerate(nums):\n            if (y := target - x) in d:\n                return [d[y], i]\n            d[x] = i\n',
  'class Solution:\n  def twoSum(self, nums: list[int], target: int) -> list[int]:\n    numToIndex = {}\n\n    for i, num in enumerate(nums):\n      if target - num in numToIndex:\n        return numToIndex[target - num], i\n      numToIndex[num] = i\n'],
 'topic_tags': ['Array', 'Hash Table'],
 'question_title': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because 

In [120]:
result = [item for item in lst if not item['completion']]
show_list(result)

List length: 17


{'slug': 'delete-columns-to-make-sorted-ii',
 'difficulty': 'Medium',
 'problem_id': 955,
 'solutions': [],
 'topic_tags': ['Greedy', 'Array', 'String'],
 'question_title': 'You are given an array of n strings strs, all of the same length.\nWe may choose any deletion indices, and we delete all the characters in those indices for each string.\nFor example, if we have strs = ["abcdef","uvwxyz"] and deletion indices {0, 2, 3}, then the final array after deletions is ["bef", "vyz"].\nSuppose we chose a set of deletion indices answer such that after deletions, the final array has its elements in lexicographic order (i.e., strs[0] <= strs[1] <= strs[2] <= ... <= strs[n - 1]). Return the minimum possible value of answer.length.\n\xa0\nExample 1:\n\nInput: strs = ["ca","bb","ac"]\nOutput: 1\nExplanation: \nAfter deleting the first column, strs = ["a", "b", "c"].\nNow strs is in lexicographic order (ie. strs[0] <= strs[1] <= strs[2]).\nWe require at least 1 deletion since initially strs was not

In [159]:
index = 16
x = result[index]
print(x['slug'])

minimum-operations-to-make-elements-within-k-subarrays-equal


In [160]:
x['completion'] = """class LazyHeap:
    def __init__(self):
        self.heap = []
        self.remove_cnt = defaultdict(int)  # 每个元素剩余需要删除的次数
        self.size = 0  # 实际大小
        self.sum = 0  # 堆中元素总和

    # 删除
    def remove(self, x: int) -> None:
        self.remove_cnt[x] += 1  # 懒删除
        self.size -= 1
        self.sum -= x

    # 正式执行删除操作
    def apply_remove(self) -> None:
        while self.heap and self.remove_cnt[self.heap[0]] > 0:
            self.remove_cnt[self.heap[0]] -= 1
            heappop(self.heap)

    # 查看堆顶
    def top(self) -> int:
        self.apply_remove()
        return self.heap[0]

    # 出堆
    def pop(self) -> int:
        self.apply_remove()
        self.size -= 1
        self.sum -= self.heap[0]
        return heappop(self.heap)

    # 入堆
    def push(self, x: int) -> None:
        if self.remove_cnt[x] > 0:
            self.remove_cnt[x] -= 1  # 抵消之前的删除
        else:
            heappush(self.heap, x)
        self.size += 1
        self.sum += x

    # push(x) 然后 pop()
    def pushpop(self, x: int) -> int:
        self.apply_remove()
        if not self.heap or x <= self.heap[0]:
            return x
        self.sum += x - self.heap[0]
        return heappushpop(self.heap, x)


class Solution:
    # 480. 滑动窗口中位数（有改动）
    # 返回 nums 的所有长为 k 的子数组的（到子数组中位数的）距离和
    def medianSlidingWindow(self, nums: list[int], k: int) -> list[int]:
        ans = [0] * (len(nums) - k + 1)
        left = LazyHeap()  # 最大堆（元素取反）
        right = LazyHeap()  # 最小堆

        for i, x in enumerate(nums):
            # 1. 进入窗口
            if left.size == right.size:
                left.push(-right.pushpop(x))
            else:
                right.push(-left.pushpop(-x))

            l = i + 1 - k
            if l < 0:  # 窗口大小不足 k
                continue

            # 2. 计算答案
            v = -left.top()
            s1 = v * left.size + left.sum  # sum 取反
            s2 = right.sum - v * right.size
            ans[l] = s1 + s2

            # 3. 离开窗口
            x = nums[l]
            if x <= -left.top():
                left.remove(-x)
                if left.size < right.size:
                    left.push(-right.pop())  # 平衡两个堆的大小
            else:
                right.remove(x)
                if left.size > right.size + 1:
                    right.push(-left.pop())  # 平衡两个堆的大小

        return ans

    def minOperations(self, nums: List[int], x: int, k: int) -> int:
        n = len(nums)
        dis = self.medianSlidingWindow(nums, x)
        f = [[0] * (n + 1) for _ in range(k + 1)]
        for i in range(1, k + 1):
            f[i][i * x - 1] = inf
            for j in range(i * x, n - (k - i) * x + 1):  # 左右留出足够空间给其他子数组
                f[i][j] = min(f[i][j - 1], f[i - 1][j - x] + dis[j - x])  # j-x 为子数组左端点
        return f[k][n]
"""

In [169]:
random.shuffle(lst)
write_jsonl('data/leetcode-metadata-2025-03-30-single-completion.jsonl', lst)

In [168]:
lst[0]

{'slug': 'two-sum',
 'difficulty': 'Easy',
 'problem_id': 1,
 'solutions': ['class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n        d = {}\n        for i, x in enumerate(nums):\n            if (y := target - x) in d:\n                return [d[y], i]\n            d[x] = i\n',
  'class Solution:\n  def twoSum(self, nums: list[int], target: int) -> list[int]:\n    numToIndex = {}\n\n    for i, num in enumerate(nums):\n      if target - num in numToIndex:\n        return numToIndex[target - num], i\n      numToIndex[num] = i\n'],
 'topic_tags': ['Array', 'Hash Table'],
 'question_title': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because 

In [111]:
from eval_lcd.data import *

lst1 = read_jsonl('data/leetcode-metadata-2025-03-30-single-completion-0-100-with-outputs.jsonl')
lst2 = read_jsonl('data/leetcode-metadata-2025-03-30-single-completion-100-500-with-outputs.jsonl')
lst3 = read_jsonl('data/leetcode-metadata-2025-03-30-single-completion-500-1000-with-outputs.jsonl')
lst4 = read_jsonl('data/leetcode-metadata-2025-03-30-single-completion-1000-1500-with-outputs.jsonl')
lst5 = read_jsonl('data/leetcode-metadata-2025-03-30-single-completion-1500-2000-with-outputs.jsonl')
lst6 = read_jsonl('data/leetcode-metadata-2025-03-30-single-completion-2000-2500-with-outputs.jsonl')
lst7 = read_jsonl('data/leetcode-metadata-2025-03-30-single-completion-2500-2600-with-outputs.jsonl') + read_jsonl('data/leetcode-metadata-2025-03-30-single-completion-2700-2800-with-outputs.jsonl') + read_jsonl('data/leetcode-metadata-2025-03-30-single-completion-2800-2900-with-outputs.jsonl') + read_jsonl('data/leetcode-metadata-2025-03-30-single-completion-2900-2945-with-outputs.jsonl')
lst8 = read_jsonl('data/leetcode-metadata-2025-03-30-single-completion-2600-2630-with-outputs.jsonl') + read_jsonl('data/leetcode-metadata-2025-03-30-single-completion-2630-2650-with-outputs.jsonl') + read_jsonl('data/leetcode-metadata-2025-03-30-single-completion-2650-2660-with-outputs.jsonl') + read_jsonl('data/leetcode-metadata-2025-03-30-single-completion-2660-2670-with-outputs.jsonl') + read_jsonl('data/leetcode-metadata-2025-03-30-single-completion-2670-2700-with-outputs.jsonl')
show_list(lst1)
show_list(lst2)
show_list(lst3)
show_list(lst4)
show_list(lst5)
show_list(lst6)
show_list(lst7)
show_list(lst8)

List length: 100
List length: 400
List length: 500
List length: 500
List length: 500
List length: 500
List length: 345
List length: 100


{'slug': 'permutations-iii',
 'difficulty': 'Medium',
 'problem_id': 3437,
 'solutions': ['class Solution:\n    def permute(self, n: int) -> List[List[int]]:\n        def dfs(i: int) -> None:\n            if i >= n:\n                ans.append(t[:])\n                return\n            for j in range(1, n + 1):\n                if not vis[j] and (i == 0 or t[-1] % 2 != j % 2):\n                    t.append(j)\n                    vis[j] = True\n                    dfs(i + 1)\n                    vis[j] = False\n                    t.pop()\n\n        ans = []\n        t = []\n        vis = [False] * (n + 1)\n        dfs(0)\n        return ans\n',
  'class Solution:\n  def permute(self, n: int) -> list[list[int]]:\n    ans = []\n    used = [False] * (n + 1)\n\n    def dfs(path: list[int]) -> None:\n      if len(path) == n:\n        ans.append(path.copy())\n        return\n      for num in range(1, n + 1):\n        if used[num]:\n          continue\n        if path and path[-1] % 2 == num

In [114]:
good, bad = [], []
for item in lst1+lst2+lst3+lst4+lst5+lst6+lst7+lst8:
    assert len(item['inputs']) == len(item['outputs'])
    inputs, outputs, assertion = [], [], []
    for a, b in zip(item['inputs'], item['outputs']):
        if b['status'] == 'success':
            inputs.append(a)
            outputs.append(b['result'])
            assertion.append(b['assertion'])
    if inputs:
        item['valid_inputs'] = inputs
        item['valid_outputs'] = outputs
        item['assertion'] = assertion
        good.append(item)
    else:
        bad.append(item)
show_list(good)
show_list(bad)


List length: 2786
List length: 159


{'slug': 'search-in-a-sorted-array-of-unknown-size',
 'difficulty': 'Medium',
 'problem_id': 702,
 'solutions': ['# """\n# This is ArrayReader\'s API interface.\n# You should not implement it, or speculate about its implementation\n# """\n# class ArrayReader:\n#    def get(self, index: int) -> int:\n\n\nclass Solution:\n    def search(self, reader: "ArrayReader", target: int) -> int:\n        r = 1\n        while reader.get(r) < target:\n            r <<= 1\n        l = r >> 1\n        while l < r:\n            mid = (l + r) >> 1\n            if reader.get(mid) >= target:\n                r = mid\n            else:\n                l = mid + 1\n        return l if reader.get(l) == target else -1\n',
  '# """\n# This is ArrayReader\'s API interface.\n# You should not implement it, or speculate about its implementation\n# """\n# Class ArrayReader:\n#   def get(self, index: int) -> int:\n\nclass Solution:\n  def search(self, reader: \'ArrayReader\', target: int) -> int:\n    l = bisect.bi

In [128]:
write_jsonl('data/leetcode-0330-good.jsonl', good)
write_jsonl('data/leetcode-0330-bad.jsonl', bad)

In [54]:
x = random.choice(result)
print(x['completion'])
print('=================================')
print(x['lang_code'])
print('=================================')
print(x['inputs'][0])
print('=================================')
print(x['outputs'][0])

class Solution:
  # Same as 3256. Maximum Value Sum by Placing Three Rooks I
  def maximumValueSum(self, board: list[list[int]]) -> int:
    rows = [heapq.nlargest(3, [(val, i, j)
            for j, val in enumerate(row)])
            for i, row in enumerate(board)]
    cols = [heapq.nlargest(3, [(val, i, j)
            for i, val in enumerate(col)])
            for j, col in enumerate(zip(*board))]
    topNine = heapq.nlargest(9,
                             set(itertools.chain(*rows)) &
                             set(itertools.chain(*cols)))
    return max(
        (val1 + val2 + val3 for
         (val1, i1, j1),
         (val2, i2, j2),
         (val3, i3, j3) in (itertools.combinations(topNine, 3))
         if len({i1, i2, i3}) == 3 and len({j1, j2, j3}) == 3))

class Solution:
    def maximumValueSum(self, board: List[List[int]]) -> int:
        
board
{'status': 'error', 'result': "Error: Solution.maximumValueSum() missing 1 required positional argument: 'board'", 'assertion': 

In [38]:
import heapq
import itertools
from sortedcontainers import SortedList

In [116]:
l1 = [item for item in good if 'TreeNode' not in item['lang_code'] and 'ListNode' not in item['lang_code']]
l2 = [item for item in good if 'TreeNode' in item['lang_code']]
l3 = [item for item in good if 'ListNode' in item['lang_code']]
show_list(l1)
show_list(l2)
show_list(l3)

List length: 2623
List length: 122
List length: 43


{'slug': 'reverse-nodes-in-even-length-groups',
 'difficulty': 'Medium',
 'problem_id': 2074,
 'solutions': ['# Definition for singly-linked list.\n# class ListNode:\n#     def __init__(self, val=0, next=None):\n#         self.val = val\n#         self.next = next\nclass Solution:\n    def reverseEvenLengthGroups(self, head: Optional[ListNode]) -> Optional[ListNode]:\n        def reverse(head, l):\n            prev, cur, tail = None, head, head\n            i = 0\n            while cur and i < l:\n                t = cur.next\n                cur.next = prev\n                prev = cur\n                cur = t\n                i += 1\n            tail.next = cur\n            return prev\n\n        n = 0\n        t = head\n        while t:\n            t = t.next\n            n += 1\n        dummy = ListNode(0, head)\n        prev = dummy\n        l = 1\n        while (1 + l) * l // 2 <= n and prev:\n            if l % 2 == 0:\n                prev.next = reverse(prev.next, l)\n        

In [125]:
result = []
for _ in range(30):
    for item in bad:
        if 'TreeNode' in item['lang_code']:
            x = random.choice(l2)
        elif 'ListNode' in item['lang_code']:
            x = random.choice(l3)
        else:
            x = random.choice(l1)
        example_desc = x['question_title'] + '\nStarter code:\n' + x['lang_code']
        example_inputs = random.sample(x['valid_inputs'], min(5, len(x['valid_inputs'])))
        problem_desc = item['question_title'] + '\nStarter code:\n' + item['lang_code']
        result.append({
            'slug': item['slug'],
            'query': prompt_gen_inputs_using_example(problem_desc=problem_desc, example_desc=example_desc, example_inputs=example_inputs)
        })
show_list(result)
result[0]

List length: 4770


{'slug': 'search-in-a-sorted-array-of-unknown-size',
 'query': 'You are an expert Python programmer. You will be given a question (including a problem specification and starter code). Your task is to generate inputs that are consistent with the problem specification and starter code. An example will be provided for illustration.\n\n**** Example ****\n\n#### Question:\nThere is an integer array perm that is a permutation of the first n positive integers, where n is always odd.\nIt was encoded into another integer array encoded of length n - 1, such that encoded[i] = perm[i] XOR perm[i + 1]. For example, if perm = [1,3,2], then encoded = [2,1].\nGiven the encoded array, return the original array perm. It is guaranteed that the answer exists and is unique.\n\xa0\nExample 1:\n\nInput: encoded = [3,1]\nOutput: [1,2,3]\nExplanation: If perm = [1,2,3], then encoded = [1 XOR 2,2 XOR 3] = [3,1]\n\nExample 2:\n\nInput: encoded = [6,5,4,6]\nOutput: [2,4,1,5,3]\n\n\xa0\nConstraints:\n\n3 <= n <\xa

In [126]:
print(result[-1]['query'])

You are an expert Python programmer. You will be given a question (including a problem specification and starter code). Your task is to generate inputs that are consistent with the problem specification and starter code. An example will be provided for illustration.

**** Example ****

#### Question:
Given the root of a binary tree, construct a 0-indexed m x n string matrix res that represents a formatted layout of the tree. The formatted layout matrix should be constructed using the following rules:

The height of the tree is height and the number of rows m should be equal to height + 1.
The number of columns n should be equal to 2height+1 - 1.
Place the root node in the middle of the top row (more formally, at location res[0][(n-1)/2]).
For each node that has been placed in the matrix at position res[r][c], place its left child at res[r+1][c-2height-r-1] and its right child at res[r+1][c+2height-r-1].
Continue this process until all the nodes in the tree have been placed.
Any empty c

In [127]:
write_jsonl('data/leetcode-0330-bad-gen-inputs-30-times.jsonl', result)

In [130]:
from utils import extract_code_blocks
from collections import defaultdict

lst1 = read_jsonl('data/leetcode-0330-bad-gen-inputs-30-times.jsonl')
lst2 = read_jsonl('vllm_predict-leetcode-0330-bad-inputs.jsonl')

id2inputs = defaultdict(set)
for a, b in zip(lst1, lst2):
    assert a['query'] == b['query']
    code_blocks = extract_code_blocks(b['output'], 'json')
    try:
        tmp = json.loads(code_blocks[0])
        if tmp:
            for text in tmp:
                id2inputs[a['slug']].add(text)
    except:
        continue
len(id2inputs)

159

In [137]:
lst = read_jsonl('data/leetcode-0330-bad.jsonl')
show_list(lst)

List length: 159


{'slug': 'search-in-a-sorted-array-of-unknown-size',
 'difficulty': 'Medium',
 'problem_id': 702,
 'solutions': ['# """\n# This is ArrayReader\'s API interface.\n# You should not implement it, or speculate about its implementation\n# """\n# class ArrayReader:\n#    def get(self, index: int) -> int:\n\n\nclass Solution:\n    def search(self, reader: "ArrayReader", target: int) -> int:\n        r = 1\n        while reader.get(r) < target:\n            r <<= 1\n        l = r >> 1\n        while l < r:\n            mid = (l + r) >> 1\n            if reader.get(mid) >= target:\n                r = mid\n            else:\n                l = mid + 1\n        return l if reader.get(l) == target else -1\n',
  '# """\n# This is ArrayReader\'s API interface.\n# You should not implement it, or speculate about its implementation\n# """\n# Class ArrayReader:\n#   def get(self, index: int) -> int:\n\nclass Solution:\n  def search(self, reader: \'ArrayReader\', target: int) -> int:\n    l = bisect.bi

In [138]:
for item in lst:
    for s in id2inputs[item['slug']]:
        if s not in item['inputs']:
            item['inputs'].append(s)
    item['prompt'] = 'import heapq\nimport itertools\nfrom sortedcontainers import SortedList\n' + item['prompt']
show_list(lst)

List length: 159


{'slug': 'search-in-a-sorted-array-of-unknown-size',
 'difficulty': 'Medium',
 'problem_id': 702,
 'solutions': ['# """\n# This is ArrayReader\'s API interface.\n# You should not implement it, or speculate about its implementation\n# """\n# class ArrayReader:\n#    def get(self, index: int) -> int:\n\n\nclass Solution:\n    def search(self, reader: "ArrayReader", target: int) -> int:\n        r = 1\n        while reader.get(r) < target:\n            r <<= 1\n        l = r >> 1\n        while l < r:\n            mid = (l + r) >> 1\n            if reader.get(mid) >= target:\n                r = mid\n            else:\n                l = mid + 1\n        return l if reader.get(l) == target else -1\n',
  '# """\n# This is ArrayReader\'s API interface.\n# You should not implement it, or speculate about its implementation\n# """\n# Class ArrayReader:\n#   def get(self, index: int) -> int:\n\nclass Solution:\n  def search(self, reader: \'ArrayReader\', target: int) -> int:\n    l = bisect.bi

In [139]:
write_jsonl('data/leetcode-0330-bad-add-inputs.jsonl', lst)

In [140]:
lst1 = read_jsonl('data/leetcode-0330-bad-add-inputs-0-40-with-outputs.jsonl')
lst2 = read_jsonl('data/leetcode-0330-bad-add-inputs-40-80-with-outputs.jsonl')
lst3 = read_jsonl('data/leetcode-0330-bad-add-inputs-80-120-with-outputs.jsonl')
lst4 = read_jsonl('data/leetcode-0330-bad-add-inputs-120-159-with-outputs.jsonl')

In [141]:
good, bad = [], []
for item in lst1+lst2+lst3+lst4:
    assert len(item['inputs']) == len(item['outputs'])
    inputs, outputs, assertion = [], [], []
    for a, b in zip(item['inputs'], item['outputs']):
        if b['status'] == 'success':
            inputs.append(a)
            outputs.append(b['result'])
            assertion.append(b['assertion'])
    if inputs:
        item['valid_inputs'] = inputs
        item['valid_outputs'] = outputs
        item['assertion'] = assertion
        good.append(item)
    else:
        bad.append(item)
show_list(good)
show_list(bad)

List length: 60
List length: 99


{'slug': 'search-in-a-sorted-array-of-unknown-size',
 'difficulty': 'Medium',
 'problem_id': 702,
 'solutions': ['# """\n# This is ArrayReader\'s API interface.\n# You should not implement it, or speculate about its implementation\n# """\n# class ArrayReader:\n#    def get(self, index: int) -> int:\n\n\nclass Solution:\n    def search(self, reader: "ArrayReader", target: int) -> int:\n        r = 1\n        while reader.get(r) < target:\n            r <<= 1\n        l = r >> 1\n        while l < r:\n            mid = (l + r) >> 1\n            if reader.get(mid) >= target:\n                r = mid\n            else:\n                l = mid + 1\n        return l if reader.get(l) == target else -1\n',
  '# """\n# This is ArrayReader\'s API interface.\n# You should not implement it, or speculate about its implementation\n# """\n# Class ArrayReader:\n#   def get(self, index: int) -> int:\n\nclass Solution:\n  def search(self, reader: \'ArrayReader\', target: int) -> int:\n    l = bisect.bi

In [142]:
write_jsonl('data/leetcode-0330-bad-good.jsonl', good)
write_jsonl('data/leetcode-0330-bad-bad.jsonl', bad)

In [143]:
x = random.choice(bad)
print(x['completion'])
print('=================================')
print(x['lang_code'])
print('=================================')
print(x['inputs'][0])
print('=================================')
print(x['outputs'][0])

class Solution:
    def rotateTheBox(self, box: List[List[str]]) -> List[List[str]]:
        m, n = len(box), len(box[0])
        ans = [[None] * m for _ in range(n)]
        for i in range(m):
            for j in range(n):
                ans[j][m - i - 1] = box[i][j]
        for j in range(m):
            q = deque()
            for i in range(n - 1, -1, -1):
                if ans[i][j] == '*':
                    q.clear()
                elif ans[i][j] == '.':
                    q.append(i)
                elif q:
                    ans[q.popleft()][j] = '#'
                    ans[i][j] = '.'
                    q.append(i)
        return ans

class Solution:
    def rotateTheBox(self, boxGrid: List[List[str]]) -> List[List[str]]:
        
boxGrid = [["#",".","*","."],["#","#","*","."]]
{'status': 'error', 'result': "Error: Solution.rotateTheBox() got an unexpected keyword argument 'boxGrid'", 'assertion': ''}


In [146]:
from data_process.prompts import lcb_style_leetcode_prompt

result = []
for _ in range(4):
    for item in bad:
        result.append({
            'slug': item['slug'],
            'query': lcb_style_leetcode_prompt(item['question_title'], item['lang_code'])
        })
show_list(result)

List length: 396


{'slug': 'search-in-a-sorted-array-of-unknown-size',
 'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nThis is an interactive problem.\nYou have a sorted array of unique elements and an unknown size. You do not have an access to the array but you can use the ArrayReader interface to access it. You can call ArrayReader.get(i) that:\n\nreturns the value at the ith index (0-indexed) of the secret array (i.e., secret[i]), or\nreturns 231 - 1 if the i is out of the boundary of the array.\n\nYou are also given an integer target.\nReturn the index k of the hidden array where secret[k] == target or return -1 otherwise.\nYou must write an algorithm with O(log n) runtime complexity.\n\xa0\nExample 1:\n\nInput: secret = [-1,0,3,5,9,12], target = 9\nOutput: 4\nExplanation: 9 exists in secret and its index is 4.\n\nExample 2:\n\nInput: 

In [147]:
write_jsonl('data/leetcode-0330-bad-bad-query-4-times.jsonl', result)

In [151]:
lst1 = read_jsonl('data/leetcode-0330-bad-bad-query-4-times.jsonl')
lst2 = read_jsonl('vllm_predict-bad-bad-4-times.jsonl')
show_list(lst1)
show_list(lst2)

List length: 396
List length: 396


{'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nThis is an interactive problem.\nYou have a sorted array of unique elements and an unknown size. You do not have an access to the array but you can use the ArrayReader interface to access it. You can call ArrayReader.get(i) that:\n\nreturns the value at the ith index (0-indexed) of the secret array (i.e., secret[i]), or\nreturns 231 - 1 if the i is out of the boundary of the array.\n\nYou are also given an integer target.\nReturn the index k of the hidden array where secret[k] == target or return -1 otherwise.\nYou must write an algorithm with O(log n) runtime complexity.\n\xa0\nExample 1:\n\nInput: secret = [-1,0,3,5,9,12], target = 9\nOutput: 4\nExplanation: 9 exists in secret and its index is 4.\n\nExample 2:\n\nInput: secret = [-1,0,3,5,9,12], target = 2\nOutput: -1\nExp

In [154]:
result = []
for a, b in zip(lst1, lst2):
    if '</think>' in b['output']:
        reasoning_content, content = b['output'].split('</think>', 1)
        code_blocks = extract_code_blocks(content, 'python3')
        code_blocks.sort(key=lambda x: len(x.split('\n')), reverse=True)
        result.append({
            'question': a['slug'],
            'lang': 'python3',
            'code': code_blocks[0] if code_blocks else content,
            'query': b['query'],
            'output': b['output'],
            'reasoning_content': reasoning_content,
            'content': content,
        })
show_list(result)

List length: 396


{'question': 'search-in-a-sorted-array-of-unknown-size',
 'lang': 'python3',
 'code': "class Solution:\n    def search(self, reader: 'ArrayReader', target: int) -> int:\n        # Check the first element\n        first_val = reader.get(0)\n        if first_val == target:\n            return 0\n        \n        # Find the high boundary using exponential search\n        high = 1\n        while True:\n            val = reader.get(high)\n            if val >= target or val == (2**31 - 1):\n                break\n            high *= 2\n        \n        # Determine the right boundary for binary search\n        if reader.get(high) == (2**31 - 1):\n            right = high - 1\n        else:\n            right = high\n        \n        left = high // 2  # Starting point for binary search\n        \n        # Binary search between left and right\n        while left <= right:\n            mid = (left + right) // 2\n            mid_val = reader.get(mid)\n            if mid_val == target:\n     

In [156]:
write_jsonl('data/question-leetcode-0330-bad-bad-query-4-times-qwq-32b.jsonl', result)

In [157]:
lst1 = read_jsonl('data/leetcode-0330-good.jsonl')
lst2 = read_jsonl('data/leetcode-0330-bad-good.jsonl')
show_list(lst1)
show_list(lst2)

List length: 2786
List length: 60


{'slug': 'closest-binary-search-tree-value',
 'difficulty': 'Easy',
 'problem_id': 270,
 'solutions': ['# Definition for a binary tree node.\n# class TreeNode:\n#     def __init__(self, val=0, left=None, right=None):\n#         self.val = val\n#         self.left = left\n#         self.right = right\nclass Solution:\n    def closestValue(self, root: Optional[TreeNode], target: float) -> int:\n        def dfs(node: Optional[TreeNode]):\n            if node is None:\n                return\n            nxt = abs(target - node.val)\n            nonlocal ans, diff\n            if nxt < diff or (nxt == diff and node.val < ans):\n                diff = nxt\n                ans = node.val\n            node = node.left if target < node.val else node.right\n            dfs(node)\n\n        ans = 0\n        diff = inf\n        dfs(root)\n        return ans\n',
  'class Solution:\n  def closestValue(self, root: TreeNode | None, target: float) -> int:\n    # If target < root.val, search the left s

In [161]:
result = []
for item in lst1+lst2:
    assert len(item['valid_inputs']) == len(item['valid_outputs']) == len(item['assertion'])
    test = 'def check(candidate):\n'
    flag = False
    for assertion in item['assertion']:
        if isinstance(assertion, str):
            test += assertion
            flag = True
    if flag:
        item['test'] = test
        result.append(item)
show_list(result)

List length: 2846


{'slug': 'distribute-elements-into-two-arrays-ii',
 'difficulty': 'Hard',
 'problem_id': 3072,
 'solutions': ['class BinaryIndexedTree:\n    __slots__ = "n", "c"\n\n    def __init__(self, n: int):\n        self.n = n\n        self.c = [0] * (n + 1)\n\n    def update(self, x: int, delta: int) -> None:\n        while x <= self.n:\n            self.c[x] += delta\n            x += x & -x\n\n    def query(self, x: int) -> int:\n        s = 0\n        while x:\n            s += self.c[x]\n            x -= x & -x\n        return s\n\n\nclass Solution:\n    def resultArray(self, nums: List[int]) -> List[int]:\n        st = sorted(set(nums))\n        m = len(st)\n        tree1 = BinaryIndexedTree(m + 1)\n        tree2 = BinaryIndexedTree(m + 1)\n        tree1.update(bisect_left(st, nums[0]) + 1, 1)\n        tree2.update(bisect_left(st, nums[1]) + 1, 1)\n        arr1 = [nums[0]]\n        arr2 = [nums[1]]\n        for x in nums[2:]:\n            i = bisect_left(st, x) + 1\n            a = len(arr

In [164]:
write_jsonl('data/leetcode-0330-valid-2846-problems.jsonl', result)

In [166]:
lst = read_jsonl('LeetCodeDataset-v0.3.0.jsonl')
show_list(lst)
print(lst[0]['test'])

List length: 2772
def check(candidate):
    assert candidate(nums = [2,7,11,15], target = 9) == [0,1]
    assert candidate(nums = [3,2,4], target = 6) == [1,2]
    assert candidate(nums = [3,3], target = 6) == [0,1]
    assert candidate(nums = [2,4,6,8,10,12,14,16,18,20,22,24,26,28,30], target = 58) == [13, 14]
    assert candidate(nums = [100, 200, 300, 400, 500, 600, 700, 800, 900, 1000], target = 1700) == [7, 8]
    assert candidate(nums = [1, 1, 2, 2, 3, 3, 4, 4, 5, 5], target = 10) == [8, 9]
    assert candidate(nums = [10,11,12,13,14,15,16,17,18,19,20], target = 30) == [4, 6]
    assert candidate(nums = [-1, -2, -3, -4, -5, -6, -7, -8, -9, -10], target = -19) == [8, 9]
    assert candidate(nums = [10, 20, 30, 40, 50, 60, 70, 80, 90, 100], target = 180) == [7, 9]
    assert candidate(nums = [5, 25, 15, 35, 45, 55, 65, 75, 85, 95], target = 100) == [4, 5]
    assert candidate(nums = [5,10,15,20,25,30,35,40,45,50], target = 95) == [8, 9]
    assert candidate(nums = [1, 3, 5, 7, 9, 1

In [185]:
lst = read_jsonl('data/leetcode-0330-valid-2846-problems.jsonl_results.jsonl')
result = [item for item in lst if not item['passed']]
r = [item for item in lst if item['passed']]
show_list(result)

List length: 19


{'slug': 'reverse-words-in-a-string',
 'difficulty': 'Medium',
 'problem_id': 151,
 'solutions': ['class Solution:\n    def reverseWords(self, s: str) -> str:\n        words = []\n        i, n = 0, len(s)\n        while i < n:\n            while i < n and s[i] == " ":\n                i += 1\n            if i < n:\n                j = i\n                while j < n and s[j] != " ":\n                    j += 1\n                words.append(s[i:j])\n                i = j\n        return " ".join(words[::-1])\n',
  "class Solution:\n  def reverseWords(self, s: str) -> str:\n    return ' '.join(reversed(s.split()))\n"],
 'topic_tags': ['Two Pointers', 'String'],
 'question_title': 'Given an input string s, reverse the order of the words.\nA word is defined as a sequence of non-space characters. The words in s will be separated by at least one space.\nReturn a string of the words in reverse order concatenated by a single space.\nNote that s may contain leading or trailing spaces or multiple

In [184]:
x = random.choice(result)
print(x['result'])
print('========================================')
print(x['test'])

failed: 
def check(candidate):
    assert candidate(s = "()())()") == ['()()()', '(())()']
    assert candidate(s = ")(") == ['']
    assert candidate(s = "(a)())()") == ['(a)()()', '(a())()']
    assert candidate(s = "(((((((((()))))))))))()()()()()()()()()()()()()()()()()()()()()()()()()()()") == ['(((((((((())))))))))()()()()()()()()()()()()()()()()()()()()()()()()()()()']
    assert candidate(s = "(()(()))())()())") == ['(((()))())(())', '(()(()))(()())', '(()(()))()()()', '(((())())()())', '(()(()))()(())', '(()(()())()())', '(()(())())()()', '(()(())()()())', '(()(())())(())', '(((()))()()())', '(((()))())()()']
    assert candidate(s = "(()))(()())))()(()())(()())") == ['(()(()()))()(()())(()())', '(())((()))()(()())(()())', '(())(()())()(()())(()())', '(((()())))()(()())(()())', '(()((())))()(()())(()())']
    assert candidate(s = "((((((((((((((((((((((((((((((((((())))))))))))))))))))))))))))))))))))))") == ['((((((((((((((((((((((((((((((((((())))))))))))))))))))))))))))))))

In [187]:
show_list(r)
write_jsonl('data/leetcode-0330-valid-2846-verified-2827.jsonl', r)

List length: 2827


In [188]:
lst1 = read_jsonl('data/leetcode-0330-good.jsonl')
lst2 = read_jsonl('data/leetcode-0330-bad.jsonl')
show_list(lst1)
show_list(lst2)

List length: 2786
List length: 159


{'slug': 'search-in-a-sorted-array-of-unknown-size',
 'difficulty': 'Medium',
 'problem_id': 702,
 'solutions': ['# """\n# This is ArrayReader\'s API interface.\n# You should not implement it, or speculate about its implementation\n# """\n# class ArrayReader:\n#    def get(self, index: int) -> int:\n\n\nclass Solution:\n    def search(self, reader: "ArrayReader", target: int) -> int:\n        r = 1\n        while reader.get(r) < target:\n            r <<= 1\n        l = r >> 1\n        while l < r:\n            mid = (l + r) >> 1\n            if reader.get(mid) >= target:\n                r = mid\n            else:\n                l = mid + 1\n        return l if reader.get(l) == target else -1\n',
  '# """\n# This is ArrayReader\'s API interface.\n# You should not implement it, or speculate about its implementation\n# """\n# Class ArrayReader:\n#   def get(self, index: int) -> int:\n\nclass Solution:\n  def search(self, reader: \'ArrayReader\', target: int) -> int:\n    l = bisect.bi

In [190]:
2786 + 159

2945

In [200]:
'You will use the following starter code to write the solution to the problem and enclose your code within delimiters'
result = []
for item in lst1+lst2:
    result.append({
        'slug': item['slug'],
        'query': lcb_style_leetcode_prompt(item['question_title'], item['lang_code']),
        'style': 'lcb'
    })
for item in lst1+lst2:
    result.append({
        'slug': item['slug'],
        'query': item['question_title'] + '\n\nPlease write the solution to the problem using the following starter code:\n```python\n' + item['lang_code'].strip() + '\n```\n',
        'style': 'normal'
    })
show_list(result)

List length: 5890


{'slug': 'distribute-elements-into-two-arrays-ii',
 'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nYou are given a 1-indexed array of integers nums of length n.\nWe define a function greaterCount such that greaterCount(arr, val) returns the number of elements in arr that are strictly greater than val.\nYou need to distribute all the elements of nums between two arrays arr1 and arr2 using n operations. In the first operation, append nums[1] to arr1. In the second operation, append nums[2] to arr2. Afterwards, in the ith operation:\n\nIf greaterCount(arr1, nums[i]) > greaterCount(arr2, nums[i]), append nums[i] to arr1.\nIf greaterCount(arr1, nums[i]) < greaterCount(arr2, nums[i]), append nums[i] to arr2.\nIf greaterCount(arr1, nums[i]) == greaterCount(arr2, nums[i]), append nums[i] to the array with a lesser number of eleme

In [202]:
write_jsonl('leetcode-0330-python-single-2945-2-style-5-times.jsonl', [item for _ in range(5) for item in result])

In [203]:
print(result[0]['query'])

You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.

### Question:
You are given a 1-indexed array of integers nums of length n.
We define a function greaterCount such that greaterCount(arr, val) returns the number of elements in arr that are strictly greater than val.
You need to distribute all the elements of nums between two arrays arr1 and arr2 using n operations. In the first operation, append nums[1] to arr1. In the second operation, append nums[2] to arr2. Afterwards, in the ith operation:

If greaterCount(arr1, nums[i]) > greaterCount(arr2, nums[i]), append nums[i] to arr1.
If greaterCount(arr1, nums[i]) < greaterCount(arr2, nums[i]), append nums[i] to arr2.
If greaterCount(arr1, nums[i]) == greaterCount(arr2, nums[i]), append nums[i] to the array with a lesser number of elements.
If there is still a tie, append nums[i] to arr1.

The array result

In [204]:
lst = read_jsonl('data/leetcode-0330-bad-bad.jsonl')
show_list(lst)

List length: 99


{'slug': 'search-in-a-sorted-array-of-unknown-size',
 'difficulty': 'Medium',
 'problem_id': 702,
 'solutions': ['# """\n# This is ArrayReader\'s API interface.\n# You should not implement it, or speculate about its implementation\n# """\n# class ArrayReader:\n#    def get(self, index: int) -> int:\n\n\nclass Solution:\n    def search(self, reader: "ArrayReader", target: int) -> int:\n        r = 1\n        while reader.get(r) < target:\n            r <<= 1\n        l = r >> 1\n        while l < r:\n            mid = (l + r) >> 1\n            if reader.get(mid) >= target:\n                r = mid\n            else:\n                l = mid + 1\n        return l if reader.get(l) == target else -1\n',
  '# """\n# This is ArrayReader\'s API interface.\n# You should not implement it, or speculate about its implementation\n# """\n# Class ArrayReader:\n#   def get(self, index: int) -> int:\n\nclass Solution:\n  def search(self, reader: \'ArrayReader\', target: int) -> int:\n    l = bisect.bi

In [219]:
x = random.choice(lst)
x

{'slug': 'maximum-frequency-score-of-a-subarray',
 'difficulty': 'Hard',
 'problem_id': 2524,
 'solutions': ['class Solution:\n    def maxFrequencyScore(self, nums: List[int], k: int) -> int:\n        mod = 10**9 + 7\n        cnt = Counter(nums[:k])\n        ans = cur = sum(pow(k, v, mod) for k, v in cnt.items()) % mod\n        i = k\n        while i < len(nums):\n            a, b = nums[i - k], nums[i]\n            if a != b:\n                cur += (b - 1) * pow(b, cnt[b], mod) if cnt[b] else b\n                cur -= (a - 1) * pow(a, cnt[a] - 1, mod) if cnt[a] > 1 else a\n                cur %= mod\n                cnt[b] += 1\n                cnt[a] -= 1\n                ans = max(ans, cur)\n            i += 1\n        return ans\n',
  "class Solution:\n  def maxFrequencyScore(self, nums: list[int], k: int) -> int:\n    MOD = 1_000_000_007\n    count = collections.Counter(nums[:k])\n    summ = self._getInitialSumm(count, MOD)\n    ans = summ\n\n    for i in range(k, len(nums)):\n  

In [ ]:
from sortedcontainers import SortedList, SortedSet, SortedDict

In [220]:
lst = read_jsonl('job_65_result_question-leetcode-0330-bad-bad-query-4-times-qwq-32b.jsonl')
show_list(lst)

List length: 396


{'response': {'status_code': 10,
  'lang': 'python3',
  'run_success': True,
  'status_runtime': '46 ms',
  'memory': 19256000,
  'question_id': '786',
  'elapsed_time': 67,
  'compare_result': '11111111111111111111111111111111111111111111111',
  'code_output': '',
  'std_output': '',
  'last_testcase': '',
  'expected_output': '',
  'task_finish_time': 1743355852239,
  'task_name': 'judger.judgetask.Judge',
  'finished': True,
  'status_msg': 'Accepted',
  'state': 'SUCCESS',
  'fast_submit': False,
  'total_correct': 47,
  'total_testcases': 47,
  'submission_id': '617324550',
  'runtime_percentile': 63.73069999999997,
  'status_memory': '18.8 MB',
  'memory_percentile': 22.28030000000002,
  'pretty_lang': 'Python3'},
 'query': {'question': 'search-in-a-sorted-array-of-unknown-size',
  'lang': 'python3',
  'code': "class Solution:\n    def search(self, reader: 'ArrayReader', target: int) -> int:\n        # Check the first element\n        first_val = reader.get(0)\n        if first_v

In [221]:
len(set(item['query']['question'] for item in lst if item['response']['status_msg'] == 'Accepted'))

88

In [222]:
id2code = {item['query']['question']: item['query']['code'] for item in lst if item['response']['status_msg'] == 'Accepted'}
len(id2code)

88

In [224]:
lst = read_jsonl('data/leetcode-0330-bad-bad.jsonl')
for item in lst:
    if item['slug'] in id2code:
        item['completion'] = id2code[item['slug']]
        item['qwq'] = True
    else:
        item['qwq'] = False
write_jsonl('data/leetcode-0330-bad-bad-qwq-completion.jsonl', lst)

In [225]:
lst = read_jsonl('data/leetcode-0330-bad-bad-qwq-completion-0-50-with-outputs.jsonl') + read_jsonl('data/leetcode-0330-bad-bad-qwq-completion-50-99-with-outputs.jsonl')
show_list(lst)

List length: 99


{'slug': 'search-in-a-sorted-array-of-unknown-size',
 'difficulty': 'Medium',
 'problem_id': 702,
 'solutions': ['# """\n# This is ArrayReader\'s API interface.\n# You should not implement it, or speculate about its implementation\n# """\n# class ArrayReader:\n#    def get(self, index: int) -> int:\n\n\nclass Solution:\n    def search(self, reader: "ArrayReader", target: int) -> int:\n        r = 1\n        while reader.get(r) < target:\n            r <<= 1\n        l = r >> 1\n        while l < r:\n            mid = (l + r) >> 1\n            if reader.get(mid) >= target:\n                r = mid\n            else:\n                l = mid + 1\n        return l if reader.get(l) == target else -1\n',
  '# """\n# This is ArrayReader\'s API interface.\n# You should not implement it, or speculate about its implementation\n# """\n# Class ArrayReader:\n#   def get(self, index: int) -> int:\n\nclass Solution:\n  def search(self, reader: \'ArrayReader\', target: int) -> int:\n    l = bisect.bi

In [227]:
good, bad = [], []
for item in lst:
    assert len(item['inputs']) == len(item['outputs'])
    inputs, outputs, assertion = [], [], []
    for a, b in zip(item['inputs'], item['outputs']):
        if b['status'] == 'success':
            inputs.append(a)
            outputs.append(b['result'])
            assertion.append(b['assertion'])
    if inputs:
        item['valid_inputs'] = inputs
        item['valid_outputs'] = outputs
        item['assertion'] = assertion
        good.append(item)
    else:
        bad.append(item)
show_list(good)
show_list(bad)

List length: 31
List length: 68


{'slug': 'search-in-a-sorted-array-of-unknown-size',
 'difficulty': 'Medium',
 'problem_id': 702,
 'solutions': ['# """\n# This is ArrayReader\'s API interface.\n# You should not implement it, or speculate about its implementation\n# """\n# class ArrayReader:\n#    def get(self, index: int) -> int:\n\n\nclass Solution:\n    def search(self, reader: "ArrayReader", target: int) -> int:\n        r = 1\n        while reader.get(r) < target:\n            r <<= 1\n        l = r >> 1\n        while l < r:\n            mid = (l + r) >> 1\n            if reader.get(mid) >= target:\n                r = mid\n            else:\n                l = mid + 1\n        return l if reader.get(l) == target else -1\n',
  '# """\n# This is ArrayReader\'s API interface.\n# You should not implement it, or speculate about its implementation\n# """\n# Class ArrayReader:\n#   def get(self, index: int) -> int:\n\nclass Solution:\n  def search(self, reader: \'ArrayReader\', target: int) -> int:\n    l = bisect.bi

In [232]:
result = []
for item in good:
    assert len(item['valid_inputs']) == len(item['valid_outputs']) == len(item['assertion'])
    test = 'def check(candidate):\n'
    flag = False
    for assertion in item['assertion']:
        if isinstance(assertion, str):
            test += assertion
            flag = True
    if flag:
        item['test'] = test
        result.append(item)
show_list(result)
write_jsonl('leetcode-0330-bad-bad-good.jsonl', result)

List length: 31


In [233]:
write_jsonl('leetcode-0330-bad-bad-bad.jsonl', bad)

In [238]:
lst2 = [item for item in read_jsonl('data/leetcode-0330-bad-bad-good.jsonl_results.jsonl') if item['passed']]
show_list(lst2)

List length: 30


{'slug': 'minimum-number-of-food-buckets-to-feed-the-hamsters',
 'difficulty': 'Medium',
 'problem_id': 2086,
 'solutions': ["class Solution:\n    def minimumBuckets(self, street: str) -> int:\n        ans = 0\n        i, n = 0, len(street)\n        while i < n:\n            if street[i] == 'H':\n                if i + 1 < n and street[i + 1] == '.':\n                    i += 2\n                    ans += 1\n                elif i and street[i - 1] == '.':\n                    ans += 1\n                else:\n                    return -1\n            i += 1\n        return ans\n",
  "class Solution:\n  def minimumBuckets(self, street: str) -> int:\n    A = list(street)\n\n    for i, c in enumerate(A):\n      if c == 'H':\n        if i > 0 and A[i - 1] == 'B':\n          continue\n        if i + 1 < len(A) and A[i + 1] == '.':\n          # Always prefer place a bucket in (i + 1) because it enhances the\n          # possibility to collect the upcoming houses.\n          A[i + 1] = 'B'\n

In [239]:
lst1 = read_jsonl('data/leetcode-0330-valid-2846-verified-2827.jsonl')
show_list(lst1)

List length: 2827


{'slug': 'count-the-digits-that-divide-a-number',
 'difficulty': 'Easy',
 'problem_id': 2520,
 'solutions': ['class Solution:\n    def countDigits(self, num: int) -> int:\n        ans, x = 0, num\n        while x:\n            x, val = divmod(x, 10)\n            ans += num % val == 0\n        return ans\n',
  'class Solution:\n  def countDigits(self, num: int) -> int:\n    return sum(num % int(d) == 0 for d in str(num))\n'],
 'topic_tags': ['Math'],
 'question_title': 'Given an integer num, return the number of digits in num that divide num.\nAn integer val divides nums if nums % val == 0.\n\xa0\nExample 1:\n\nInput: num = 7\nOutput: 1\nExplanation: 7 divides itself, hence the answer is 1.\n\nExample 2:\n\nInput: num = 121\nOutput: 2\nExplanation: 121 is divisible by 1, but not 2. Since 1 occurs twice as a digit, we return 2.\n\nExample 3:\n\nInput: num = 1248\nOutput: 4\nExplanation: 1248 is divisible by all of its digits, hence the answer is 4.\n\n\xa0\nConstraints:\n\n1 <= num <= 10

In [240]:
write_jsonl('data/leetcode-0330-verified-2857.jsonl', lst1+lst2)

In [242]:
lst1 = [item for item in read_jsonl('data/leetcode-0330-valid-2846-problems.jsonl_results.jsonl') if not item['passed']]
lst2 = read_jsonl('data/leetcode-0330-bad-bad-bad.jsonl')
show_list(lst1)
show_list(lst2)

List length: 19
List length: 68


{'slug': 'search-in-a-sorted-array-of-unknown-size',
 'difficulty': 'Medium',
 'problem_id': 702,
 'solutions': ['# """\n# This is ArrayReader\'s API interface.\n# You should not implement it, or speculate about its implementation\n# """\n# class ArrayReader:\n#    def get(self, index: int) -> int:\n\n\nclass Solution:\n    def search(self, reader: "ArrayReader", target: int) -> int:\n        r = 1\n        while reader.get(r) < target:\n            r <<= 1\n        l = r >> 1\n        while l < r:\n            mid = (l + r) >> 1\n            if reader.get(mid) >= target:\n                r = mid\n            else:\n                l = mid + 1\n        return l if reader.get(l) == target else -1\n',
  '# """\n# This is ArrayReader\'s API interface.\n# You should not implement it, or speculate about its implementation\n# """\n# Class ArrayReader:\n#   def get(self, index: int) -> int:\n\nclass Solution:\n  def search(self, reader: \'ArrayReader\', target: int) -> int:\n    l = bisect.bi

In [243]:
write_jsonl('data/leetcode-0330-unverified-87.jsonl', lst1+lst2)

In [244]:
lst1 = read_jsonl('data/leetcode-0330-verified-2857.jsonl')
lst2 = read_jsonl('LeetCodeDataset-v0.3.0.jsonl')
show_list(lst1)
show_list(lst2)

List length: 2857
List length: 2772


{'task_id': 'two-sum',
 'question_id': 1,
 'difficulty': 'Easy',
 'tags': ['Array', 'Hash Table'],
 'problem_description': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?',
 'starter_code': 'class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:',
 

In [246]:
s1 = set(item['task_id'] for item in lst1)
s2 = set(item['task_id'] for item in lst2)
len(s1), len(s2), len(s1 | s2)

(2857, 2772, 2872)

In [254]:
result = []
for item in lst1:
    assert len(item['inputs']) == len(item['outputs'])
    tmp = []
    for i, o in zip(item['inputs'], item['outputs']):
        tmp.append({
            'input': i,
            'output': o['result']
        })
    result.append({
        'task_id': item['task_id'],
        'question_id': item['problem_id'],
        'difficulty': item['difficulty'],
        'tags': item['topic_tags'],
        'problem_description': item['question_title'],
        'starter_code': item['lang_code'],
        'estimated_date': '',
        'prompt': item['prompt'],
        'completion': item['completion'],
        'entry_point': item['entry_point'],
        'test': item['test'],
        'input_output': tmp,
        'query': lcb_style_leetcode_prompt(item['question_title'], item['lang_code']),
        'response': ''
    })
show_list(result)

List length: 2857


{'task_id': 'count-the-digits-that-divide-a-number',
 'question_id': 2520,
 'difficulty': 'Easy',
 'tags': ['Math'],
 'problem_description': 'Given an integer num, return the number of digits in num that divide num.\nAn integer val divides nums if nums % val == 0.\n\xa0\nExample 1:\n\nInput: num = 7\nOutput: 1\nExplanation: 7 divides itself, hence the answer is 1.\n\nExample 2:\n\nInput: num = 121\nOutput: 2\nExplanation: 121 is divisible by 1, but not 2. Since 1 occurs twice as a digit, we return 2.\n\nExample 3:\n\nInput: num = 1248\nOutput: 4\nExplanation: 1248 is divisible by all of its digits, hence the answer is 4.\n\n\xa0\nConstraints:\n\n1 <= num <= 109\nnum does not contain 0 as one of its digits.\n\n',
 'starter_code': 'class Solution:\n    def countDigits(self, num: int) -> int:\n        ',
 'estimated_date': '',
 'prompt': "import random\nimport functools\nimport collections\nimport string\nimport math\nimport datetime\n\nfrom typing import *\nfrom functools import *\nfrom 

In [255]:
write_jsonl('data/leetcode-0330-verified-2857-formated.jsonl', result)

In [258]:
s = s2 - s1
for item in lst2:
    if item['task_id'] in s:
        result.append(item)
show_list(result)

List length: 2872


{'task_id': 'count-the-digits-that-divide-a-number',
 'question_id': 2520,
 'difficulty': 'Easy',
 'tags': ['Math'],
 'problem_description': 'Given an integer num, return the number of digits in num that divide num.\nAn integer val divides nums if nums % val == 0.\n\xa0\nExample 1:\n\nInput: num = 7\nOutput: 1\nExplanation: 7 divides itself, hence the answer is 1.\n\nExample 2:\n\nInput: num = 121\nOutput: 2\nExplanation: 121 is divisible by 1, but not 2. Since 1 occurs twice as a digit, we return 2.\n\nExample 3:\n\nInput: num = 1248\nOutput: 4\nExplanation: 1248 is divisible by all of its digits, hence the answer is 4.\n\n\xa0\nConstraints:\n\n1 <= num <= 109\nnum does not contain 0 as one of its digits.\n\n',
 'starter_code': 'class Solution:\n    def countDigits(self, num: int) -> int:\n        ',
 'estimated_date': '',
 'prompt': "import random\nimport functools\nimport collections\nimport string\nimport math\nimport datetime\n\nfrom typing import *\nfrom functools import *\nfrom 

In [259]:
write_jsonl('data/leetcode-0330-combined-verified-2872-formated.jsonl', result)

In [260]:
id2date = {item['task_id']: item['estimated_date'] for item in lst2}
len(id2date)

2772

In [262]:
from leetcode_functions import get_week_contest_question_title
from datetime import datetime, timedelta

In [263]:
(datetime(2025, 3, 2) + timedelta(days=7)).strftime('%Y-%m-%d')

datetime.datetime(2025, 3, 9, 0, 0)

In [264]:
get_week_contest_question_title(439)

[{'credit': 3,
  'question_id': 3705,
  'title': 'find-the-largest-almost-missing-integer',
  'title_cn': '找出最大的几近缺失整数'},
 {'credit': 4,
  'question_id': 3786,
  'title': 'longest-palindromic-subsequence-after-at-most-k-operations',
  'title_cn': '至多 K 次操作后的最长回文子序列'},
 {'credit': 5,
  'question_id': 3722,
  'title': 'sum-of-k-subarrays-with-length-at-least-m',
  'title_cn': '长度至少为 M 的 K 个子数组之和'},
 {'credit': 7,
  'question_id': 3770,
  'title': 'lexicographically-smallest-generated-string',
  'title_cn': '字典序最小的生成字符串'}]

In [266]:
for week in range(439, 444):
    date = (datetime(2025, 3, 2) + timedelta(days=7*(week-439))).strftime("%Y-%m-%d")
    for item in get_week_contest_question_title(week=week):
        id2date[item['title']] = date
len(id2date)

2784

In [267]:
lst = read_jsonl('data/leetcode-0330-combined-verified-2872-formated.jsonl')
show_list(lst)

List length: 2872


{'task_id': 'count-the-digits-that-divide-a-number',
 'question_id': 2520,
 'difficulty': 'Easy',
 'tags': ['Math'],
 'problem_description': 'Given an integer num, return the number of digits in num that divide num.\nAn integer val divides nums if nums % val == 0.\n\xa0\nExample 1:\n\nInput: num = 7\nOutput: 1\nExplanation: 7 divides itself, hence the answer is 1.\n\nExample 2:\n\nInput: num = 121\nOutput: 2\nExplanation: 121 is divisible by 1, but not 2. Since 1 occurs twice as a digit, we return 2.\n\nExample 3:\n\nInput: num = 1248\nOutput: 4\nExplanation: 1248 is divisible by all of its digits, hence the answer is 4.\n\n\xa0\nConstraints:\n\n1 <= num <= 109\nnum does not contain 0 as one of its digits.\n\n',
 'starter_code': 'class Solution:\n    def countDigits(self, num: int) -> int:\n        ',
 'estimated_date': '',
 'prompt': "import random\nimport functools\nimport collections\nimport string\nimport math\nimport datetime\n\nfrom typing import *\nfrom functools import *\nfrom 

In [269]:
lst.sort(key=lambda x: x['question_id'])
lst[0]

{'task_id': 'two-sum',
 'question_id': 1,
 'difficulty': 'Easy',
 'tags': ['Array', 'Hash Table'],
 'problem_description': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?',
 'starter_code': 'class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n  

In [270]:
pre_date = None
for item in lst:
    task_id = item['task_id']
    if task_id in id2date:
        item['estimated_date'] = id2date[task_id]
        pre_date = id2date[task_id]
    else:
        item['estimated_date'] = pre_date
show_list(lst)

List length: 2872


{'task_id': 'two-sum',
 'question_id': 1,
 'difficulty': 'Easy',
 'tags': ['Array', 'Hash Table'],
 'problem_description': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?',
 'starter_code': 'class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n  

In [272]:
for i, item in enumerate(lst):
    print(item['estimated_date'])

2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07
2015-08-07

In [285]:
lst = read_jsonl('LeetCodeDataset-v0.3.1.jsonl')
result = [item for item in lst if item['task_id'] in s]
show_list(result)

List length: 2870


{'task_id': 'two-sum',
 'question_id': 1,
 'difficulty': 'Easy',
 'tags': ['Array', 'Hash Table'],
 'problem_description': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?',
 'starter_code': 'class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n  

In [286]:
write_jsonl('LeetCodeDataset-v0.3.1.jsonl', result)

In [288]:
lst = read_jsonl('LeetCodeDataset-v0.3.1.jsonl')
s = set(item['task_id'] for item in lst)
len(s)

2870

In [275]:
lst1 = read_jsonl('leetcode-0330-python-single-2945-2-style-5-times.jsonl')
lst2 = read_jsonl('vllm_predict-0330-2945-2-style-3-times.jsonl')
show_list(lst1)
show_list(lst2)

List length: 29450
List length: 17670


{'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nYou are given a 1-indexed array of integers nums of length n.\nWe define a function greaterCount such that greaterCount(arr, val) returns the number of elements in arr that are strictly greater than val.\nYou need to distribute all the elements of nums between two arrays arr1 and arr2 using n operations. In the first operation, append nums[1] to arr1. In the second operation, append nums[2] to arr2. Afterwards, in the ith operation:\n\nIf greaterCount(arr1, nums[i]) > greaterCount(arr2, nums[i]), append nums[i] to arr1.\nIf greaterCount(arr1, nums[i]) < greaterCount(arr2, nums[i]), append nums[i] to arr2.\nIf greaterCount(arr1, nums[i]) == greaterCount(arr2, nums[i]), append nums[i] to the array with a lesser number of elements.\nIf there is still a tie, append nums[i] to ar

In [277]:
lst1[0]

{'slug': 'distribute-elements-into-two-arrays-ii',
 'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nYou are given a 1-indexed array of integers nums of length n.\nWe define a function greaterCount such that greaterCount(arr, val) returns the number of elements in arr that are strictly greater than val.\nYou need to distribute all the elements of nums between two arrays arr1 and arr2 using n operations. In the first operation, append nums[1] to arr1. In the second operation, append nums[2] to arr2. Afterwards, in the ith operation:\n\nIf greaterCount(arr1, nums[i]) > greaterCount(arr2, nums[i]), append nums[i] to arr1.\nIf greaterCount(arr1, nums[i]) < greaterCount(arr2, nums[i]), append nums[i] to arr2.\nIf greaterCount(arr1, nums[i]) == greaterCount(arr2, nums[i]), append nums[i] to the array with a lesser number of eleme

In [291]:
from eval_lcd.data import extract_completion

result = []
for a, b in zip(lst1, lst2):
    assert a['query'] == b['query']
    if a['style'] == 'normal' and a['slug'] in s:
        if '</think>' in b['output']:
            reasoning_content, content = b['output'].split('</think>', 1)
        else:
            content = b['output']
        result.append({
            'task_id': a['slug'],
            'query': b['query'],
            'output': b['output'],
            'content': content,
            'completion': extract_completion(content)
        })
show_list(result)

List length: 8610


{'task_id': 'distribute-elements-into-two-arrays-ii',
 'query': 'You are given a 1-indexed array of integers nums of length n.\nWe define a function greaterCount such that greaterCount(arr, val) returns the number of elements in arr that are strictly greater than val.\nYou need to distribute all the elements of nums between two arrays arr1 and arr2 using n operations. In the first operation, append nums[1] to arr1. In the second operation, append nums[2] to arr2. Afterwards, in the ith operation:\n\nIf greaterCount(arr1, nums[i]) > greaterCount(arr2, nums[i]), append nums[i] to arr1.\nIf greaterCount(arr1, nums[i]) < greaterCount(arr2, nums[i]), append nums[i] to arr2.\nIf greaterCount(arr1, nums[i]) == greaterCount(arr2, nums[i]), append nums[i] to the array with a lesser number of elements.\nIf there is still a tie, append nums[i] to arr1.\n\nThe array result is formed by concatenating the arrays arr1 and arr2. For example, if arr1 == [1,2,3] and arr2 == [4,5,6], then result = [1,2,3

In [292]:
write_jsonl('leetcode-2870-qwq-normal-3-times-completion.jsonl', result)

In [293]:
lst1 = read_jsonl('LeetCodeDataset-v0.3.0.jsonl')
lst2 = read_jsonl('LeetCodeDataset-v0.3.1.jsonl')
show_list(lst1)
show_list(lst2)

List length: 2772
List length: 2870


{'task_id': 'two-sum',
 'question_id': 1,
 'difficulty': 'Easy',
 'tags': ['Array', 'Hash Table'],
 'problem_description': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?',
 'starter_code': 'class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n  

In [298]:
result = [{'task_id': item['task_id'], 'query': item['query']} for item in lst2]
write_jsonl('leetcode-2870-lcb-query.jsonl', result)
show_list(result)

List length: 2870


{'task_id': 'two-sum',
 'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nGiven an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time com

In [299]:
lst1 = read_jsonl('leetcode-2870-lcb-query.jsonl')
lst2 = read_jsonl('vllm_predict-2870-32b-lcb.jsonl')
show_list(lst2)

List length: 2870


{'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nGiven an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?\n\n### Format:

In [301]:
for a, b in zip(lst1, lst2):
    a['output'] = b['output']
    a['completion'] = extract_completion(b['output'])
show_list(lst1)
write_jsonl('leetcode-2870-lcb-completion.jsonl', lst1)

List length: 2870


In [303]:
x = random.choice(lst1)
print(x['output'])

```python
# Definition for singly-linked list.
# class ListNode:
#     def __init__(self, val=0, next=None):
#         self.val = val
#         self.next = next
class Solution:
    def deleteDuplicatesUnsorted(self, head: Optional[ListNode]) -> Optional[ListNode]:
        # First pass: count the occurrences of each value
        value_count = {}
        current = head
        while current:
            value_count[current.val] = value_count.get(current.val, 0) + 1
            current = current.next
        
        # Second pass: remove nodes with values that appear more than once
        dummy = ListNode(0)
        dummy.next = head
        prev = dummy
        current = head
        
        while current:
            if value_count[current.val] > 1:
                prev.next = current.next  # Skip this node
            else:
                prev = current  # Move prev only if we keep the current node
            current = current.next
        
        return dummy.next
```

This sol

In [304]:
import numpy as np

lst = read_jsonl('LeetCodeDataset-v0.3.1.jsonl')
show_list(lst)

List length: 2870


{'task_id': 'two-sum',
 'question_id': 1,
 'difficulty': 'Easy',
 'tags': ['Array', 'Hash Table'],
 'problem_description': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?',
 'starter_code': 'class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n  

In [313]:
nums = [len(item['input_output']) for item in lst]
np.mean(nums), np.min(nums), np.max(nums)

(100.57038327526132, 3, 451)

In [316]:
l = [item for item in lst if len(item['input_output']) < 10]
show_list(l)

List length: 5


{'task_id': 'generate-parentheses',
 'question_id': 22,
 'difficulty': 'Medium',
 'tags': ['String', 'Dynamic Programming', 'Backtracking'],
 'problem_description': 'Given n pairs of parentheses, write a function to generate all combinations of well-formed parentheses.\n\xa0\nExample 1:\nInput: n = 3\nOutput: ["((()))","(()())","(())()","()(())","()()()"]\nExample 2:\nInput: n = 1\nOutput: ["()"]\n\n\xa0\nConstraints:\n\n1 <= n <= 8\n\n',
 'starter_code': 'class Solution:\n    def generateParenthesis(self, n: int) -> List[str]:\n        ',
 'estimated_date': '2015-08-07',
 'prompt': "import random\nimport functools\nimport collections\nimport string\nimport math\nimport datetime\n\nfrom typing import *\nfrom functools import *\nfrom collections import *\nfrom itertools import *\nfrom heapq import *\nfrom bisect import *\nfrom string import *\nfrom operator import *\nfrom math import *\n\ninf = float('inf')\n\nclass ListNode:\n    def __init__(self, val=0, next=None):\n        self.val 

In [317]:
lst = read_jsonl('LeetCodeDataset-v0.3.1.jsonl_results.jsonl')
show_list(lst)

List length: 2870


{'task_id': 'two-sum',
 'question_id': 1,
 'difficulty': 'Easy',
 'tags': ['Array', 'Hash Table'],
 'problem_description': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?',
 'starter_code': 'class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n  

In [318]:
l = [item for item in lst if not item['passed']]
show_list(l)

List length: 30


{'task_id': 'sudoku-solver',
 'question_id': 37,
 'difficulty': 'Hard',
 'tags': ['Array', 'Hash Table', 'Backtracking', 'Matrix'],
 'problem_description': 'Write a program to solve a Sudoku puzzle by filling the empty cells.\nA sudoku solution must satisfy all of the following rules:\n\nEach of the digits 1-9 must occur exactly once in each row.\nEach of the digits 1-9 must occur exactly once in each column.\nEach of the digits 1-9 must occur exactly once in each of the 9 3x3 sub-boxes of the grid.\n\nThe \'.\' character indicates empty cells.\n\xa0\nExample 1:\n\n\nInput: board = [["5","3",".",".","7",".",".",".","."],["6",".",".","1","9","5",".",".","."],[".","9","8",".",".",".",".","6","."],["8",".",".",".","6",".",".",".","3"],["4",".",".","8",".","3",".",".","1"],["7",".",".",".","2",".",".",".","6"],[".","6",".",".",".",".","2","8","."],[".",".",".","4","1","9",".",".","5"],[".",".",".",".","8",".",".","7","9"]]\nOutput: [["5","3","4","6","7","8","9","1","2"],["6","7","2","1","9

In [319]:
result = []
for i, item in enumerate(l):
    print(i, item['result'], len(item['input_output']))

0 timed out 42
1 failed:  29
2 timed out 151
3 timed out 127
4 timed out 153
5 timed out 102
6 timed out 82
7 timed out 60
8 timed out 71
9 timed out 121
10 timed out 102
11 timed out 93
12 timed out 66
13 timed out 84
14 timed out 115
15 timed out 98
16 timed out 100
17 timed out 93
18 timed out 123
19 timed out 95
20 timed out 213
21 timed out 91
22 timed out 89
23 timed out 88
24 timed out 92
25 timed out 100
26 timed out 102
27 timed out 113
28 timed out 103
29 timed out 111


In [321]:
x = l[1]
print(x['prompt'] + '\n' + x['completion'] + '\n' + x['test'])

import random
import functools
import collections
import string
import math
import datetime

from typing import *
from functools import *
from collections import *
from itertools import *
from heapq import *
from bisect import *
from string import *
from operator import *
from math import *

inf = float('inf')

class ListNode:
    def __init__(self, val=0, next=None):
        self.val = val
        self.next = next

def list_node(values: list):
    if not values:
        return None
    head = ListNode(values[0])
    p = head
    for val in values[1:]:
        node = ListNode(val)
        p.next = node
        p = node
    return head

def is_same_list(p1, p2):
    if p1 is None and p2 is None:
        return True
    if not p1 or not p2:
        return False
    return p1.val == p2.val and is_same_list(p1.next, p2.next)

class TreeNode:
    def __init__(self, val=0, left=None, right=None):
        self.val = val
        self.left = left
        self.right = right

def tree_node(values

In [333]:
from data_process.compute_output import process_input
from data_process.execution import execute_function
from tqdm import tqdm

item = x
code = item['prompt'] + '\n' + item['completion']
lang_code = item['starter_code']
entry_point = item['entry_point']
tmp = []
for s in tqdm(item['input_output']):
    input_str = s['input']
    params, assertion = process_input(input_str, lang_code, entry_point)
    output = execute_function(code, entry_point, params, assertion)
    tmp.append(output)
print(tmp)

100%|██████████| 29/29 [00:02<00:00, 10.82it/s]

[{'status': 'success', 'result': "[['red', 'ted', 'tex', 'tax'], ['red', 'rex', 'tex', 'tax'], ['red', 'ted', 'tad', 'tax']]", 'assertion': '    assert candidate(beginWord = "red",endWord = "tax",wordList = [\'ted\', \'tex\', \'red\', \'tax\', \'tad\', \'den\', \'rex\', \'pee\']) == [[\'red\', \'ted\', \'tex\', \'tax\'], [\'red\', \'rex\', \'tex\', \'tax\'], [\'red\', \'ted\', \'tad\', \'tax\']]\n'}, {'status': 'success', 'result': '[]', 'assertion': '    assert candidate(beginWord = "red",endWord = "tax",wordList = [\'ted\', \'tex\', \'red\', \'tad\', \'den\', \'rex\', \'pee\']) == []\n'}, {'status': 'success', 'result': "[['a', 'c']]", 'assertion': '    assert candidate(beginWord = "a",endWord = "c",wordList = [\'a\', \'b\', \'c\']) == [[\'a\', \'c\']]\n'}, {'status': 'success', 'result': '[]', 'assertion': '    assert candidate(beginWord = "hit",endWord = "cog",wordList = [\'hot\', \'dot\', \'dog\', \'lot\', \'log\']) == []\n'}, {'status': 'success', 'result': "[['hot', 'dot', 'dog'

In [337]:
input_output = []
assertion = ""
for a, b in zip(item['input_output'], tmp):
    input_output.append({
        'input': a['input'],
        'output': b['result']
    })
    assertion += b['assertion']
input_output

[{'input': 'beginWord = "red", endWord = "tax", wordList = ["ted","tex","red","tax","tad","den","rex","pee"]',
  'output': "[['red', 'ted', 'tex', 'tax'], ['red', 'rex', 'tex', 'tax'], ['red', 'ted', 'tad', 'tax']]"},
 {'input': 'beginWord = "red", endWord = "tax", wordList = ["ted","tex","red","tad","den","rex","pee"]',
  'output': '[]'},
 {'input': 'beginWord = "a", endWord = "c", wordList = ["a","b","c"]',
  'output': "[['a', 'c']]"},
 {'input': 'beginWord = "hit", endWord = "cog", wordList = ["hot","dot","dog","lot","log"]',
  'output': '[]'},
 {'input': 'beginWord = "hot", endWord = "dog", wordList = ["hot","dog","dot"]',
  'output': "[['hot', 'dot', 'dog']]"},
 {'input': 'beginWord = "hit", endWord = "cog", wordList = ["hot","dot","dog","lot","log","cog"]',
  'output': "[['hit', 'hot', 'dot', 'dog', 'cog'], ['hit', 'hot', 'lot', 'log', 'cog']]"},
 {'input': 'beginWord = "start", endWord = "reach", wordList = ["stark","tark","park","peck","pack","pace","pece","reck","peel","peak",

In [340]:
assertion = "def check(candidate):\n" + assertion

In [341]:
print(x['prompt'] + '\n' + x['completion'] + '\n' + assertion)

import random
import functools
import collections
import string
import math
import datetime

from typing import *
from functools import *
from collections import *
from itertools import *
from heapq import *
from bisect import *
from string import *
from operator import *
from math import *

inf = float('inf')

class ListNode:
    def __init__(self, val=0, next=None):
        self.val = val
        self.next = next

def list_node(values: list):
    if not values:
        return None
    head = ListNode(values[0])
    p = head
    for val in values[1:]:
        node = ListNode(val)
        p.next = node
        p = node
    return head

def is_same_list(p1, p2):
    if p1 is None and p2 is None:
        return True
    if not p1 or not p2:
        return False
    return p1.val == p2.val and is_same_list(p1.next, p2.next)

class TreeNode:
    def __init__(self, val=0, left=None, right=None):
        self.val = val
        self.left = left
        self.right = right

def tree_node(values

In [345]:
lst = read_jsonl('LeetCodeDataset-v0.3.1.jsonl_results.jsonl')
show_list(lst)

List length: 2870


{'task_id': 'two-sum',
 'question_id': 1,
 'difficulty': 'Easy',
 'tags': ['Array', 'Hash Table'],
 'problem_description': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?',
 'starter_code': 'class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n  

In [346]:
result = [item for item in lst if item['passed']]
show_list(result)

List length: 2869


{'task_id': 'two-sum',
 'question_id': 1,
 'difficulty': 'Easy',
 'tags': ['Array', 'Hash Table'],
 'problem_description': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?',
 'starter_code': 'class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n  

In [347]:
write_jsonl('LeetCodeDataset-v0.3.1.jsonl', result)

In [360]:
lst = read_jsonl('data/leetcode-0330-unverified-87.jsonl')
show_list(lst)

List length: 87


{'slug': 'reverse-words-in-a-string',
 'difficulty': 'Medium',
 'problem_id': 151,
 'solutions': ['class Solution:\n    def reverseWords(self, s: str) -> str:\n        words = []\n        i, n = 0, len(s)\n        while i < n:\n            while i < n and s[i] == " ":\n                i += 1\n            if i < n:\n                j = i\n                while j < n and s[j] != " ":\n                    j += 1\n                words.append(s[i:j])\n                i = j\n        return " ".join(words[::-1])\n',
  "class Solution:\n  def reverseWords(self, s: str) -> str:\n    return ' '.join(reversed(s.split()))\n"],
 'topic_tags': ['Two Pointers', 'String'],
 'question_title': 'Given an input string s, reverse the order of the words.\nA word is defined as a sequence of non-space characters. The words in s will be separated by at least one space.\nReturn a string of the words in reverse order concatenated by a single space.\nNote that s may contain leading or trailing spaces or multiple

In [361]:
result = []
for item in lst:
    item['prompt'] = 'from sortedcontainers import SortedList, SortedSet, SortedDict\n' + item['prompt']
    if 'valid_outputs' in item:
        l1, l2, l3 = [], [], []
        assert len(item['valid_inputs']) == len(item['valid_outputs']) == len(item['assertion'])
        for input_str, output_str, assertion in zip(item['valid_inputs'], item['valid_outputs'], item['assertion']):
            if isinstance(input_str, str) and isinstance(output_str, str) and isinstance(assertion, str):
                if '\n' not in input_str and '\n' not in output_str and '\n' not in assertion.strip():
                    l1.append(input_str)
                    l2.append(output_str)
                    l3.append('    ' + assertion.strip())
        item['test'] = 'def check(candidate):\n' + '\n'.join(l3)
        item['valid_inputs'] = l1
        item['valid_outputs'] = l2
        result.append(item)
show_list(result)

List length: 19


{'slug': 'reverse-words-in-a-string',
 'difficulty': 'Medium',
 'problem_id': 151,
 'solutions': ['class Solution:\n    def reverseWords(self, s: str) -> str:\n        words = []\n        i, n = 0, len(s)\n        while i < n:\n            while i < n and s[i] == " ":\n                i += 1\n            if i < n:\n                j = i\n                while j < n and s[j] != " ":\n                    j += 1\n                words.append(s[i:j])\n                i = j\n        return " ".join(words[::-1])\n',
  "class Solution:\n  def reverseWords(self, s: str) -> str:\n    return ' '.join(reversed(s.split()))\n"],
 'topic_tags': ['Two Pointers', 'String'],
 'question_title': 'Given an input string s, reverse the order of the words.\nA word is defined as a sequence of non-space characters. The words in s will be separated by at least one space.\nReturn a string of the words in reverse order concatenated by a single space.\nNote that s may contain leading or trailing spaces or multiple

In [362]:
write_jsonl('data/leetcode-0330-valid-2846-unverified.jsonl', result)

In [376]:
lst = [item for item in read_jsonl('data/leetcode-0330-valid-2846-unverified.jsonl_results.jsonl') if item['passed']]
show_list(lst)

List length: 4


{'slug': 'reverse-words-in-a-string',
 'difficulty': 'Medium',
 'problem_id': 151,
 'solutions': ['class Solution:\n    def reverseWords(self, s: str) -> str:\n        words = []\n        i, n = 0, len(s)\n        while i < n:\n            while i < n and s[i] == " ":\n                i += 1\n            if i < n:\n                j = i\n                while j < n and s[j] != " ":\n                    j += 1\n                words.append(s[i:j])\n                i = j\n        return " ".join(words[::-1])\n',
  "class Solution:\n  def reverseWords(self, s: str) -> str:\n    return ' '.join(reversed(s.split()))\n"],
 'topic_tags': ['Two Pointers', 'String'],
 'question_title': 'Given an input string s, reverse the order of the words.\nA word is defined as a sequence of non-space characters. The words in s will be separated by at least one space.\nReturn a string of the words in reverse order concatenated by a single space.\nNote that s may contain leading or trailing spaces or multiple

In [378]:
result = []
for item in lst:
    assert len(item['inputs']) == len(item['outputs'])
    tmp = []
    for i, o in zip(item['inputs'], item['outputs']):
        tmp.append({
            'input': i,
            'output': o['result']
        })
    result.append({
        'task_id': item['task_id'],
        'question_id': item['problem_id'],
        'difficulty': item['difficulty'],
        'tags': item['topic_tags'],
        'problem_description': item['question_title'],
        'starter_code': item['lang_code'],
        'estimated_date': '',
        'prompt': item['prompt'],
        'completion': item['completion'],
        'entry_point': item['entry_point'],
        'test': item['test'],
        'input_output': tmp,
        'query': lcb_style_leetcode_prompt(item['question_title'], item['lang_code']),
        'response': ''
    })
result[-1]


{'task_id': 'longest-absolute-file-path',
 'question_id': 388,
 'difficulty': 'Medium',
 'tags': ['Stack', 'Depth-First Search', 'String'],
 'problem_description': 'Suppose we have a file system that stores both files and directories. An example of one system is represented in the following picture:\n\nHere, we have dir as the only directory in the root. dir contains two subdirectories, subdir1 and subdir2. subdir1 contains a file file1.ext and subdirectory subsubdir1. subdir2 contains a subdirectory subsubdir2, which contains a file file2.ext.\nIn text form, it looks like this (with ⟶ representing the tab character):\n\ndir\n⟶ subdir1\n⟶ ⟶ file1.ext\n⟶ ⟶ subsubdir1\n⟶ subdir2\n⟶ ⟶ subsubdir2\n⟶ ⟶ ⟶ file2.ext\n\nIf we were to write this representation in code, it will look like this: "dir\\\n\\\tsubdir1\\\n\\\t\\\tfile1.ext\\\n\\\t\\\tsubsubdir1\\\n\\\tsubdir2\\\n\\\t\\\tsubsubdir2\\\n\\\t\\\t\\\tfile2.ext". Note that the \'\\\n\' and \'\\\t\' are the new-line and tab characters.\nEver

In [366]:
write_jsonl('tmp.jsonl', result)

In [367]:
lst = read_jsonl('LeetCodeDataset-2869-v0.3.1.jsonl') + read_jsonl('tmp.jsonl')
lst.sort(key=lambda x: x['question_id'])
show_list(lst)

List length: 2873


{'task_id': 'two-sum',
 'question_id': 1,
 'difficulty': 'Easy',
 'tags': ['Array', 'Hash Table'],
 'problem_description': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?',
 'starter_code': 'class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n  

In [368]:
pre_date = None
for item in lst:
    task_id = item['task_id']
    if task_id in id2date:
        item['estimated_date'] = id2date[task_id]
        pre_date = id2date[task_id]
    else:
        item['estimated_date'] = pre_date
show_list(lst)

List length: 2873


{'task_id': 'two-sum',
 'question_id': 1,
 'difficulty': 'Easy',
 'tags': ['Array', 'Hash Table'],
 'problem_description': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?',
 'starter_code': 'class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n  

In [371]:
write_jsonl('LeetCodeDataset-v0.3.1.jsonl', lst)

In [372]:
lst = read_jsonl('LeetCodeDataset-v0.3.1.jsonl_results.jsonl')
result = [item for item in lst if not item['passed']]
show_list(result)

List length: 1


{'task_id': 'reverse-words-in-a-string',
 'question_id': 151,
 'difficulty': 'Medium',
 'tags': ['Two Pointers', 'String'],
 'problem_description': 'Given an input string s, reverse the order of the words.\nA word is defined as a sequence of non-space characters. The words in s will be separated by at least one space.\nReturn a string of the words in reverse order concatenated by a single space.\nNote that s may contain leading or trailing spaces or multiple spaces between two words. The returned string should only have a single space separating the words. Do not include any extra spaces.\n\xa0\nExample 1:\n\nInput: s = "the sky is blue"\nOutput: "blue is sky the"\n\nExample 2:\n\nInput: s = "  hello world  "\nOutput: "world hello"\nExplanation: Your reversed string should not contain leading or trailing spaces.\n\nExample 3:\n\nInput: s = "a good   example"\nOutput: "example good a"\nExplanation: You need to reduce multiple spaces between two words to a single space in the reversed st

In [379]:
s1 = set(item['task_id'] for item in lst)
s1

{'length-of-last-word',
 'longest-absolute-file-path',
 'reverse-words-in-a-string',
 'strong-password-checker-ii'}

In [384]:
s = set(item['query'] for item in read_jsonl('LeetCodeDataset-v0.3.1.jsonl'))
len(s)

2869

In [390]:
result = [item for item in read_jsonl('LeetCodeDataset-v0.3.1.jsonl_results.jsonl') if not item['passed']]
show_list(result)

List length: 2


{'task_id': 'closest-subsequence-sum',
 'question_id': 1755,
 'difficulty': 'Hard',
 'tags': ['Bit Manipulation',
  'Array',
  'Two Pointers',
  'Dynamic Programming',
  'Bitmask',
  'Sorting'],
 'problem_description': "You are given an integer array nums and an integer goal.\nYou want to choose a subsequence of nums such that the sum of its elements is the closest possible to goal. That is, if the sum of the subsequence's elements is sum, then you want to minimize the absolute difference abs(sum - goal).\nReturn the minimum possible value of abs(sum - goal).\nNote that a subsequence of an array is an array formed by removing some elements (possibly all or none) of the original array.\n\xa0\nExample 1:\n\nInput: nums = [5,-7,3,5], goal = 6\nOutput: 0\nExplanation: Choose the whole array as a subsequence, with a sum of 6.\nThis is equal to the goal, so the absolute difference is 0.\n\nExample 2:\n\nInput: nums = [7,-9,15,-2], goal = -5\nOutput: 1\nExplanation: Choose the subsequence [7,

In [391]:
result[1]

{'task_id': 'next-greater-numerically-balanced-number',
 'question_id': 2048,
 'difficulty': 'Medium',
 'tags': ['Hash Table', 'Math', 'Backtracking', 'Counting', 'Enumeration'],
 'problem_description': 'An integer x is numerically balanced if for every digit d in the number x, there are exactly d occurrences of that digit in x.\nGiven an integer n, return the smallest numerically balanced number strictly greater than n.\n\xa0\nExample 1:\n\nInput: n = 1\nOutput: 22\nExplanation: \n22 is numerically balanced since:\n- The digit 2 occurs 2 times. \nIt is also the smallest numerically balanced number strictly greater than 1.\n\nExample 2:\n\nInput: n = 1000\nOutput: 1333\nExplanation: \n1333 is numerically balanced since:\n- The digit 1 occurs 1 time.\n- The digit 3 occurs 3 times. \nIt is also the smallest numerically balanced number strictly greater than 1000.\nNote that 1022 cannot be the answer because 0 appeared more than 0 times.\n\nExample 3:\n\nInput: n = 3000\nOutput: 3133\nExpl

In [385]:
lst1 = [item for item in read_jsonl('vllm_predict-2870-32b-9-times.jsonl') + read_jsonl('vllm_predict-2870-32b-lcb.jsonl') if item['query'] in s]
show_list(lst1)

List length: 28690


{'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nGiven an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?\n\n### Format:

In [386]:
lst2 = read_jsonl('LeetCodeDataset-v0.3.1.jsonl')

In [388]:
for i, a  in enumerate(lst1):
    b = lst2[i % 2869]
    assert a['query'] == b['query']
    a['task_id'] = b['task_id']
    a['completion'] = extract_completion(a['output'])
show_list(lst1)

List length: 28690


{'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nGiven an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?\n\n### Format:

In [392]:
write_jsonl('leetcode-2869-qwen-32b-10-times-lcb.jsonl', lst1)

In [393]:
lst = read_jsonl('LeetCodeDataset-v0.3.1.jsonl')
show_list(lst)

List length: 2869


{'task_id': 'two-sum',
 'question_id': 1,
 'difficulty': 'Easy',
 'tags': ['Array', 'Hash Table'],
 'problem_description': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?',
 'starter_code': 'class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n  

In [396]:
for item in lst:
    del item['result']
    del item['passed']
    item['query'] = lcb_style_leetcode_prompt(question_title=item['problem_description'], lang_code=item['starter_code'])

In [397]:
result = [item for item in lst if item['estimated_date'] >= '2024-07-01']
show_list(result)

List length: 256


{'task_id': 'find-the-encrypted-string',
 'question_id': 3210,
 'difficulty': 'Easy',
 'tags': ['String'],
 'problem_description': 'You are given a string s and an integer k. Encrypt the string using the following algorithm:\n\nFor each character c in s, replace c with the kth character after c in the string (in a cyclic manner).\n\nReturn the encrypted string.\n\xa0\nExample 1:\n\nInput: s = "dart", k = 3\nOutput: "tdar"\nExplanation:\n\nFor i = 0, the 3rd character after \'d\' is \'t\'.\nFor i = 1, the 3rd character after \'a\' is \'d\'.\nFor i = 2, the 3rd character after \'r\' is \'a\'.\nFor i = 3, the 3rd character after \'t\' is \'r\'.\n\n\nExample 2:\n\nInput: s = "aaa", k = 1\nOutput: "aaa"\nExplanation:\nAs all the characters are the same, the encrypted string will also be the same.\n\n\xa0\nConstraints:\n\n1 <= s.length <= 100\n1 <= k <= 104\ns consists only of lowercase English letters.\n\n',
 'starter_code': 'class Solution:\n    def getEncryptedString(self, s: str, k: int)

In [398]:
print(result[0]['query'])

You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.

### Question:
You are given a string s and an integer k. Encrypt the string using the following algorithm:

For each character c in s, replace c with the kth character after c in the string (in a cyclic manner).

Return the encrypted string.
 
Example 1:

Input: s = "dart", k = 3
Output: "tdar"
Explanation:

For i = 0, the 3rd character after 'd' is 't'.
For i = 1, the 3rd character after 'a' is 'd'.
For i = 2, the 3rd character after 'r' is 'a'.
For i = 3, the 3rd character after 't' is 'r'.


Example 2:

Input: s = "aaa", k = 1
Output: "aaa"
Explanation:
As all the characters are the same, the encrypted string will also be the same.

 
Constraints:

1 <= s.length <= 100
1 <= k <= 104
s consists only of lowercase English letters.



### Format: You will use the following starter code to write the solu

In [400]:
write_jsonl('LeetCodeDataset-v0.3.1.jsonl', lst)

In [401]:
result = []
for _ in range(10):
    for item in lst:
        result.append({
            'task_id': item['task_id'],
            'query': item['query']
        })
show_list(result)

List length: 28690


{'task_id': 'two-sum',
 'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nGiven an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time com

In [402]:
write_jsonl('leetcode-2869-10-times-query.jsonl', result)

In [403]:
lst1 = read_jsonl('leetcode-2869-10-times-query.jsonl')
lst2 = read_jsonl('vllm_predict-2869-qwen-10-times.jsonl')
show_list(lst1)
show_list(lst2)

List length: 28690
List length: 28690


{'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nGiven an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?\n\n### Format:

In [404]:
for a, b in zip(lst1, lst2):
    b['task_id'] = a['task_id']
    b['completion'] = extract_completion(b['output'])
show_list(lst2)

List length: 28690


{'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nGiven an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?\n\n### Format:

In [405]:
write_jsonl('vllm_predict-2869-qwen-10-times.jsonl', lst2)

In [406]:
lst = read_jsonl('vllm_predict-2869-qwen-10-times.jsonl_results.jsonl')
show_list(lst)

List length: 28690


{'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nGiven an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?\n\n### Format:

In [409]:
s = set(item['task_id'] for item in lst if item['passed'])
len(s)

2333

In [412]:
2869 - 2333

536

In [410]:
lst = read_jsonl('vllm_predict-2869-qwen-10-times.jsonl')
show_list(lst)

List length: 28690


{'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nGiven an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?\n\n### Format:

In [411]:
result = [item for item in lst if item['task_id'] not in s]
show_list(result)

List length: 5360


{'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nGiven a string s, return the longest palindromic substring in s.\n\xa0\nExample 1:\n\nInput: s = "babad"\nOutput: "bab"\nExplanation: "aba" is also a valid answer.\n\nExample 2:\n\nInput: s = "cbbd"\nOutput: "bb"\n\n\xa0\nConstraints:\n\n1 <= s.length <= 1000\ns consist of only digits and English letters.\n\n\n\n### Format: You will use the following starter code to write the solution to the problem and enclose your code within delimiters.\n```python\nclass Solution:\n    def longestPalindrome(self, s: str) -> str:\n        \n```\n\n### Answer: (use the provided format with backticks)\n',
 'prompt': '<|im_start|>system\nYou are Qwen, created by Alibaba Cloud. You are a helpful assistant.<|im_end|>\n<|im_start|>user\nYou are an expert Python programmer. You will be given a qu

In [413]:
write_jsonl('leetcode-2869-unsolve-536-5-times-query.jsonl', result[: len(result) // 2])

In [426]:
lst = read_jsonl('leetcode-2869-unsolve-536-5-times-query-2025-03-31-21-03-23-1.0-deepseek-v3-250324.jsonl-tmp.jsonl')
show_list(lst)

List length: 2680


{'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nYou are given the heads of two sorted linked lists list1 and list2.\nMerge the two lists into one sorted list. The list should be made by splicing together the nodes of the first two lists.\nReturn the head of the merged linked list.\n\xa0\nExample 1:\n\n\nInput: list1 = [1,2,4], list2 = [1,3,4]\nOutput: [1,1,2,3,4,4]\n\nExample 2:\n\nInput: list1 = [], list2 = []\nOutput: []\n\nExample 3:\n\nInput: list1 = [], list2 = [0]\nOutput: [0]\n\n\xa0\nConstraints:\n\nThe number of nodes in both lists is in the range [0, 50].\n-100 <= Node.val <= 100\nBoth list1 and list2 are sorted in non-decreasing order.\n\n\n\n### Format: You will use the following starter code to write the solution to the problem and enclose your code within delimiters.\n```python\n# Definition for singly-linke

In [427]:
from collections import defaultdict

cnt = 0
info = defaultdict(list)
for item in lst:
    if item:
        k = item['query']
        v = item['output']
        if k and v and item['meta']['choices'][0]['finish_reason'] == 'stop':
            info[k].append(v)
            cnt += 1

In [428]:
l = read_jsonl('leetcode-2869-unsolve-536-5-times-query.jsonl')
show_list(l)
cnt = 0
for item in l:
    query = item['query']
    del item['prompt']
    if query in info and info[query]:
        v = info[query]
        output = v.pop()
        item['output'] = output
        item['completion'] = extract_completion(output)
    else:
        item['output'] = ''
        item['completion'] = ''
        cnt += 1
    item['model_id'] = 'deepseek-v3-0324'
print(cnt)
write_jsonl("leetcode-2869-unsolve-536-5-times-deepseek-v3-0324.jsonl", l)
show_list(l)

List length: 2680
12
List length: 2680


{'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nGiven a string s, return the longest palindromic substring in s.\n\xa0\nExample 1:\n\nInput: s = "babad"\nOutput: "bab"\nExplanation: "aba" is also a valid answer.\n\nExample 2:\n\nInput: s = "cbbd"\nOutput: "bb"\n\n\xa0\nConstraints:\n\n1 <= s.length <= 1000\ns consist of only digits and English letters.\n\n\n\n### Format: You will use the following starter code to write the solution to the problem and enclose your code within delimiters.\n```python\nclass Solution:\n    def longestPalindrome(self, s: str) -> str:\n        \n```\n\n### Answer: (use the provided format with backticks)\n',
 'output': 'To solve this problem, we need to find the longest palindromic substring in a given string. A palindrome is a string that reads the same backward as forward. The approach involv

In [429]:
s = set(item['task_id'] for item in l)
len(s)

536

In [430]:
lst = read_jsonl('LeetCodeDataset-v0.3.1.jsonl')
show_list(lst)

List length: 2869


{'task_id': 'two-sum',
 'question_id': 1,
 'difficulty': 'Easy',
 'tags': ['Array', 'Hash Table'],
 'problem_description': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?',
 'starter_code': 'class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n  

In [432]:
result = [item for item in lst if item['task_id'] in s]
show_list(result)
write_jsonl('leetcode-2869-unsolve-536-problems.jsonl', result)

List length: 536


In [451]:
lst1 = read_jsonl('leetcode-2869-unsolve-536-5-times-query.jsonl')
lst2 = read_jsonl('vllm_predict-30.jsonl') + read_jsonl('vllm_predict-50.jsonl')
show_list(lst1)
show_list(lst2)

result = []
for i, item in enumerate(lst2):
    x = lst1[i % 536]
    assert x['query'] == item['query']
    item['task_id'] = x['task_id']
    item['completion'] = extract_completion(item['output'])
    if item['task_id'] not in id2tgt:
        result.append(item)
show_list(result)

List length: 2680
List length: 42880
List length: 33680


{'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nGiven a string s, return the longest palindromic substring in s.\n\xa0\nExample 1:\n\nInput: s = "babad"\nOutput: "bab"\nExplanation: "aba" is also a valid answer.\n\nExample 2:\n\nInput: s = "cbbd"\nOutput: "bb"\n\n\xa0\nConstraints:\n\n1 <= s.length <= 1000\ns consist of only digits and English letters.\n\n\n\n### Format: You will use the following starter code to write the solution to the problem and enclose your code within delimiters.\n```python\nclass Solution:\n    def longestPalindrome(self, s: str) -> str:\n        \n```\n\n### Answer: (use the provided format with backticks)\n',
 'output': '```python\nclass Solution:\n    def longestPalindrome(self, s: str) -> str:\n        if not s or len(s) == 1:\n            return s\n        \n        def expand_around_center(l

In [452]:
write_jsonl('leetcode-2869-unsolve-536-bad-32b-80-times.jsonl', result)

In [441]:
write_jsonl('vllm_predict-536-32b-20-times.jsonl', lst2)

In [446]:
lst = read_jsonl('vllm_predict-536-32b-20-times.jsonl_results.jsonl')
show_list(lst)

List length: 10720


{'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nGiven a string s, return the longest palindromic substring in s.\n\xa0\nExample 1:\n\nInput: s = "babad"\nOutput: "bab"\nExplanation: "aba" is also a valid answer.\n\nExample 2:\n\nInput: s = "cbbd"\nOutput: "bb"\n\n\xa0\nConstraints:\n\n1 <= s.length <= 1000\ns consist of only digits and English letters.\n\n\n\n### Format: You will use the following starter code to write the solution to the problem and enclose your code within delimiters.\n```python\nclass Solution:\n    def longestPalindrome(self, s: str) -> str:\n        \n```\n\n### Answer: (use the provided format with backticks)\n',
 'output': '```python\nclass Solution:\n    def longestPalindrome(self, s: str) -> str:\n        if not s or len(s) == 1:\n            return s\n        \n        def expand_around_center(l

In [447]:
id2tgt = {item['task_id']: item['output'] for item in lst if item['passed']}
len(id2tgt)

115

In [448]:
lst = read_jsonl('leetcode-2869-unsolve-536-problems.jsonl')
show_list(lst)

List length: 536


{'task_id': 'longest-palindromic-substring',
 'question_id': 5,
 'difficulty': 'Medium',
 'tags': ['Two Pointers', 'String', 'Dynamic Programming'],
 'problem_description': 'Given a string s, return the longest palindromic substring in s.\n\xa0\nExample 1:\n\nInput: s = "babad"\nOutput: "bab"\nExplanation: "aba" is also a valid answer.\n\nExample 2:\n\nInput: s = "cbbd"\nOutput: "bb"\n\n\xa0\nConstraints:\n\n1 <= s.length <= 1000\ns consist of only digits and English letters.\n\n',
 'starter_code': 'class Solution:\n    def longestPalindrome(self, s: str) -> str:\n        ',
 'estimated_date': '2015-08-07',
 'prompt': "import random\nimport functools\nimport collections\nimport string\nimport math\nimport datetime\n\nfrom typing import *\nfrom functools import *\nfrom collections import *\nfrom itertools import *\nfrom heapq import *\nfrom bisect import *\nfrom string import *\nfrom operator import *\nfrom math import *\n\ninf = float('inf')\n\nclass ListNode:\n    def __init__(self, v

In [449]:
good, bad = [], []
for item in lst:
    task_id = item['task_id']
    if task_id in id2tgt:
        item['response'] = id2tgt[task_id]
        good.append(item)
    else:
        bad.append(item)
show_list(good)

List length: 115


{'task_id': 'permutations',
 'question_id': 46,
 'difficulty': 'Medium',
 'tags': ['Array', 'Backtracking'],
 'problem_description': 'Given an array nums of distinct integers, return all the possible permutations. You can return the answer in any order.\n\xa0\nExample 1:\nInput: nums = [1,2,3]\nOutput: [[1,2,3],[1,3,2],[2,1,3],[2,3,1],[3,1,2],[3,2,1]]\nExample 2:\nInput: nums = [0,1]\nOutput: [[0,1],[1,0]]\nExample 3:\nInput: nums = [1]\nOutput: [[1]]\n\n\xa0\nConstraints:\n\n1 <= nums.length <= 6\n-10 <= nums[i] <= 10\nAll the integers of nums are unique.\n\n',
 'starter_code': 'class Solution:\n    def permute(self, nums: List[int]) -> List[List[int]]:\n        ',
 'estimated_date': '2015-08-07',
 'prompt': "import random\nimport functools\nimport collections\nimport string\nimport math\nimport datetime\n\nfrom typing import *\nfrom functools import *\nfrom collections import *\nfrom itertools import *\nfrom heapq import *\nfrom bisect import *\nfrom string import *\nfrom operator im

In [450]:
write_jsonl('leetcode-2869-unsolve-536-problems-good.jsonl', good)
write_jsonl('leetcode-2869-unsolve-536-problems-bad.jsonl', bad)

In [455]:
x = lst[0]
print(x['prompt'] + '\n' + x['completion'] + '\n' + x['test'])

import random
import functools
import collections
import string
import math
import datetime

from typing import *
from functools import *
from collections import *
from itertools import *
from heapq import *
from bisect import *
from string import *
from operator import *
from math import *

inf = float('inf')

class ListNode:
    def __init__(self, val=0, next=None):
        self.val = val
        self.next = next

def list_node(values: list):
    if not values:
        return None
    head = ListNode(values[0])
    p = head
    for val in values[1:]:
        node = ListNode(val)
        p.next = node
        p = node
    return head

def is_same_list(p1, p2):
    if p1 is None and p2 is None:
        return True
    if not p1 or not p2:
        return False
    return p1.val == p2.val and is_same_list(p1.next, p2.next)

class TreeNode:
    def __init__(self, val=0, left=None, right=None):
        self.val = val
        self.left = left
        self.right = right

def tree_node(values

In [456]:
lst = read_jsonl('leetcode-2869-unsolve-536-bad-32b-80-times.jsonl_results.jsonl')
show_list(lst)

List length: 33680


{'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nGiven a string s, return the longest palindromic substring in s.\n\xa0\nExample 1:\n\nInput: s = "babad"\nOutput: "bab"\nExplanation: "aba" is also a valid answer.\n\nExample 2:\n\nInput: s = "cbbd"\nOutput: "bb"\n\n\xa0\nConstraints:\n\n1 <= s.length <= 1000\ns consist of only digits and English letters.\n\n\n\n### Format: You will use the following starter code to write the solution to the problem and enclose your code within delimiters.\n```python\nclass Solution:\n    def longestPalindrome(self, s: str) -> str:\n        \n```\n\n### Answer: (use the provided format with backticks)\n',
 'output': '```python\nclass Solution:\n    def longestPalindrome(self, s: str) -> str:\n        if not s or len(s) == 1:\n            return s\n        \n        def expand_around_center(l

In [457]:
id2tgt = {item['task_id']: item['output'] for item in lst if item['passed']}
len(id2tgt)

48

In [465]:
lst = read_jsonl('LeetCodeDataset-v0.3.1.jsonl')
show_list(lst)

List length: 2869


{'task_id': 'two-sum',
 'question_id': 1,
 'difficulty': 'Easy',
 'tags': ['Array', 'Hash Table'],
 'problem_description': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?',
 'starter_code': 'class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n  

In [466]:
for item in lst:
    item['response'] = ''
write_jsonl('LeetCodeDataset-v0.3.1.jsonl', lst)

In [467]:
lst1 = read_jsonl('vllm_predict-2869-qwen-10-times.jsonl_results.jsonl')
lst2 = read_jsonl('vllm_predict-536-32b-20-times.jsonl_results.jsonl')
lst3 = read_jsonl('leetcode-2869-unsolve-536-bad-32b-80-times.jsonl_results.jsonl')
show_list(lst1)
show_list(lst2)
show_list(lst3)

List length: 28690
List length: 10720
List length: 33680


{'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nGiven a string s, return the longest palindromic substring in s.\n\xa0\nExample 1:\n\nInput: s = "babad"\nOutput: "bab"\nExplanation: "aba" is also a valid answer.\n\nExample 2:\n\nInput: s = "cbbd"\nOutput: "bb"\n\n\xa0\nConstraints:\n\n1 <= s.length <= 1000\ns consist of only digits and English letters.\n\n\n\n### Format: You will use the following starter code to write the solution to the problem and enclose your code within delimiters.\n```python\nclass Solution:\n    def longestPalindrome(self, s: str) -> str:\n        \n```\n\n### Answer: (use the provided format with backticks)\n',
 'output': '```python\nclass Solution:\n    def longestPalindrome(self, s: str) -> str:\n        if not s or len(s) == 1:\n            return s\n        \n        def expand_around_center(l

In [468]:
info = defaultdict(list)
for item in lst1+lst2+lst3:
    if item['passed']:
        info[item['task_id']].append(item['output'])
len(info)

2496

In [469]:
lst = read_jsonl('LeetCodeDataset-v0.3.1.jsonl')
show_list(lst)

List length: 2869


{'task_id': 'two-sum',
 'question_id': 1,
 'difficulty': 'Easy',
 'tags': ['Array', 'Hash Table'],
 'problem_description': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?',
 'starter_code': 'class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n  

In [470]:
import random

for item in lst:
    task_id = item['task_id']
    if task_id in info:
        item['response'] = random.choice(info[task_id])
show_list(lst)

List length: 2869


{'task_id': 'two-sum',
 'question_id': 1,
 'difficulty': 'Easy',
 'tags': ['Array', 'Hash Table'],
 'problem_description': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?',
 'starter_code': 'class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n  

In [471]:
write_jsonl('LeetCodeDataset-v0.3.1.jsonl', lst)

In [472]:
print(lst[1000]['query'])

You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.

### Question:
Given three integer arrays arr1, arr2 and arr3 sorted in strictly increasing order, return a sorted array of only the integers that appeared in all three arrays.
 
Example 1:

Input: arr1 = [1,2,3,4,5], arr2 = [1,2,5,7,9], arr3 = [1,3,4,5,8]
Output: [1,5]
Explanation: Only 1 and 5 appeared in the three arrays.

Example 2:

Input: arr1 = [197,418,523,876,1356], arr2 = [501,880,1593,1710,1870], arr3 = [521,682,1337,1395,1764]
Output: []

 
Constraints:

1 <= arr1.length, arr2.length, arr3.length <= 1000
1 <= arr1[i], arr2[i], arr3[i] <= 2000



### Format: You will use the following starter code to write the solution to the problem and enclose your code within delimiters.
```python
class Solution:
    def arraysIntersection(self, arr1: List[int], arr2: List[int], arr3: List[int]) -> List[in

In [476]:
result = []
for _ in range(100):
    for item in lst:
        if not item['response']:
            result.append({
                'task_id': item['task_id'],
                'query': item['query'].replace('### Answer: (use the provided format with backticks)', '### Hint:\n' + item['completion'].strip() + '\n\n### Answer: (use the provided format with backticks)')
            })
write_jsonl('leetcode-2869-unsolve-373-100-times-hint-query.jsonl', result)
show_list(result)

List length: 37300


{'task_id': 'longest-palindromic-substring',
 'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nGiven a string s, return the longest palindromic substring in s.\n\xa0\nExample 1:\n\nInput: s = "babad"\nOutput: "bab"\nExplanation: "aba" is also a valid answer.\n\nExample 2:\n\nInput: s = "cbbd"\nOutput: "bb"\n\n\xa0\nConstraints:\n\n1 <= s.length <= 1000\ns consist of only digits and English letters.\n\n\n\n### Format: You will use the following starter code to write the solution to the problem and enclose your code within delimiters.\n```python\nclass Solution:\n    def longestPalindrome(self, s: str) -> str:\n        \n```\n\n### Hint:\nclass Solution:\n    def longestPalindrome(self, s: str) -> str:\n        n = len(s)\n        f = [[True] * n for _ in range(n)]\n        k, mx = 0, 1\n        for i in range(n - 2, -1, -1):

In [477]:
lst = read_jsonl('LeetCodeDataset-v0.3.1.jsonl')
show_list(lst)

List length: 2869


{'task_id': 'two-sum',
 'question_id': 1,
 'difficulty': 'Easy',
 'tags': ['Array', 'Hash Table'],
 'problem_description': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?',
 'starter_code': 'class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n  

In [478]:
result = [item for item in lst if item['estimated_date'] >= '2024-07-01']
show_list(result)

List length: 256


{'task_id': 'find-the-encrypted-string',
 'question_id': 3210,
 'difficulty': 'Easy',
 'tags': ['String'],
 'problem_description': 'You are given a string s and an integer k. Encrypt the string using the following algorithm:\n\nFor each character c in s, replace c with the kth character after c in the string (in a cyclic manner).\n\nReturn the encrypted string.\n\xa0\nExample 1:\n\nInput: s = "dart", k = 3\nOutput: "tdar"\nExplanation:\n\nFor i = 0, the 3rd character after \'d\' is \'t\'.\nFor i = 1, the 3rd character after \'a\' is \'d\'.\nFor i = 2, the 3rd character after \'r\' is \'a\'.\nFor i = 3, the 3rd character after \'t\' is \'r\'.\n\n\nExample 2:\n\nInput: s = "aaa", k = 1\nOutput: "aaa"\nExplanation:\nAs all the characters are the same, the encrypted string will also be the same.\n\n\xa0\nConstraints:\n\n1 <= s.length <= 100\n1 <= k <= 104\ns consists only of lowercase English letters.\n\n',
 'starter_code': 'class Solution:\n    def getEncryptedString(self, s: str, k: int)

In [479]:
write_jsonl('LeetCodeDataset-v0.3.1-test.jsonl', result)

In [481]:
x = random.choice(result)
print(x['query'])

You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.

### Question:
Given a string s, calculate its reverse degree.
The reverse degree is calculated as follows:

For each character, multiply its position in the reversed alphabet ('a' = 26, 'b' = 25, ..., 'z' = 1) with its position in the string (1-indexed).
Sum these products for all characters in the string.

Return the reverse degree of s.
 
Example 1:

Input: s = "abc"
Output: 148
Explanation:



Letter
Index in Reversed Alphabet
Index in String
Product


'a'
26
1
26


'b'
25
2
50


'c'
24
3
72



The reversed degree is 26 + 50 + 72 = 148.

Example 2:

Input: s = "zaza"
Output: 160
Explanation:



Letter
Index in Reversed Alphabet
Index in String
Product


'z'
1
1
1


'a'
26
2
52


'z'
1
3
3


'a'
26
4
104



The reverse degree is 1 + 52 + 3 + 104 = 160.

 
Constraints:

1 <= s.length <= 1000
s contain

In [482]:
lst1 = read_jsonl('LeetCodeDataset-v0.3.1-test.jsonl')
lst2 = read_jsonl('LeetCodeDataset-v0.3.1-test-2025-04-01-23-58-33-0.95-deepseek-v3-250324.jsonl')
show_list(lst1)
show_list(lst2)

List length: 256
List length: 256


{'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nYou are given a string s and an integer k. Encrypt the string using the following algorithm:\n\nFor each character c in s, replace c with the kth character after c in the string (in a cyclic manner).\n\nReturn the encrypted string.\n\xa0\nExample 1:\n\nInput: s = "dart", k = 3\nOutput: "tdar"\nExplanation:\n\nFor i = 0, the 3rd character after \'d\' is \'t\'.\nFor i = 1, the 3rd character after \'a\' is \'d\'.\nFor i = 2, the 3rd character after \'r\' is \'a\'.\nFor i = 3, the 3rd character after \'t\' is \'r\'.\n\n\nExample 2:\n\nInput: s = "aaa", k = 1\nOutput: "aaa"\nExplanation:\nAs all the characters are the same, the encrypted string will also be the same.\n\n\xa0\nConstraints:\n\n1 <= s.length <= 100\n1 <= k <= 104\ns consists only of lowercase English letters.\n\n\n\

In [483]:
for a, b in zip(lst1, lst2):
    b['task_id'] = a['task_id']
    b['completion'] = extract_completion(b['output'])
write_jsonl('LeetCodeDataset-v0.3.1-test-2025-04-01-23-58-33-0.95-deepseek-v3-250324.jsonl', lst2)

In [487]:
deepseek_v3_0324 = [50, 52, 64.52, 42.86, 42.31, 52.94, 57.69, 37.04, 48.39]

In [488]:
lst1 = read_jsonl('leetcode-2869-unsolve-373-100-times-hint-query.jsonl')
lst2 = read_jsonl('vllm_predict-373-32b-100-times.jsonl')
show_list(lst1)
show_list(lst2)

List length: 37300
List length: 37300


{'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nGiven a string s, return the longest palindromic substring in s.\n\xa0\nExample 1:\n\nInput: s = "babad"\nOutput: "bab"\nExplanation: "aba" is also a valid answer.\n\nExample 2:\n\nInput: s = "cbbd"\nOutput: "bb"\n\n\xa0\nConstraints:\n\n1 <= s.length <= 1000\ns consist of only digits and English letters.\n\n\n\n### Format: You will use the following starter code to write the solution to the problem and enclose your code within delimiters.\n```python\nclass Solution:\n    def longestPalindrome(self, s: str) -> str:\n        \n```\n\n### Hint:\nclass Solution:\n    def longestPalindrome(self, s: str) -> str:\n        n = len(s)\n        f = [[True] * n for _ in range(n)]\n        k, mx = 0, 1\n        for i in range(n - 2, -1, -1):\n            for j in range(i + 1, n):\n    

In [489]:
for a, b in zip(lst1, lst2):
    b['task_id'] = a['task_id']
    b['completion'] = extract_completion(b['output'])
show_list(lst2)

List length: 37300


{'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nGiven a string s, return the longest palindromic substring in s.\n\xa0\nExample 1:\n\nInput: s = "babad"\nOutput: "bab"\nExplanation: "aba" is also a valid answer.\n\nExample 2:\n\nInput: s = "cbbd"\nOutput: "bb"\n\n\xa0\nConstraints:\n\n1 <= s.length <= 1000\ns consist of only digits and English letters.\n\n\n\n### Format: You will use the following starter code to write the solution to the problem and enclose your code within delimiters.\n```python\nclass Solution:\n    def longestPalindrome(self, s: str) -> str:\n        \n```\n\n### Hint:\nclass Solution:\n    def longestPalindrome(self, s: str) -> str:\n        n = len(s)\n        f = [[True] * n for _ in range(n)]\n        k, mx = 0, 1\n        for i in range(n - 2, -1, -1):\n            for j in range(i + 1, n):\n    

In [490]:
write_jsonl('vllm_predict-373-32b-100-times.jsonl', lst2)

In [491]:
lst = [item for item in read_jsonl('LeetCodeDataset-v0.3.1.jsonl') if not item['response']]
show_list(lst)

List length: 373


{'task_id': 'longest-palindromic-substring',
 'question_id': 5,
 'difficulty': 'Medium',
 'tags': ['Two Pointers', 'String', 'Dynamic Programming'],
 'problem_description': 'Given a string s, return the longest palindromic substring in s.\n\xa0\nExample 1:\n\nInput: s = "babad"\nOutput: "bab"\nExplanation: "aba" is also a valid answer.\n\nExample 2:\n\nInput: s = "cbbd"\nOutput: "bb"\n\n\xa0\nConstraints:\n\n1 <= s.length <= 1000\ns consist of only digits and English letters.\n\n',
 'starter_code': 'class Solution:\n    def longestPalindrome(self, s: str) -> str:\n        ',
 'estimated_date': '2015-08-07',
 'prompt': "import random\nimport functools\nimport collections\nimport string\nimport math\nimport datetime\n\nfrom typing import *\nfrom functools import *\nfrom collections import *\nfrom itertools import *\nfrom heapq import *\nfrom bisect import *\nfrom string import *\nfrom operator import *\nfrom math import *\n\ninf = float('inf')\n\nclass ListNode:\n    def __init__(self, v

In [492]:
write_jsonl('leetcode-2869-unsolve-373-problems.jsonl', lst)

In [493]:
lst = read_jsonl('vllm_predict-373-32b-10-times.jsonl_results.jsonl')
show_list(lst)

List length: 3730


{'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nGiven a string s, return the longest palindromic substring in s.\n\xa0\nExample 1:\n\nInput: s = "babad"\nOutput: "bab"\nExplanation: "aba" is also a valid answer.\n\nExample 2:\n\nInput: s = "cbbd"\nOutput: "bb"\n\n\xa0\nConstraints:\n\n1 <= s.length <= 1000\ns consist of only digits and English letters.\n\n\n\n### Format: You will use the following starter code to write the solution to the problem and enclose your code within delimiters.\n```python\nclass Solution:\n    def longestPalindrome(self, s: str) -> str:\n        \n```\n\n### Hint:\nclass Solution:\n    def longestPalindrome(self, s: str) -> str:\n        n = len(s)\n        f = [[True] * n for _ in range(n)]\n        k, mx = 0, 1\n        for i in range(n - 2, -1, -1):\n            for j in range(i + 1, n):\n    

In [494]:
info = defaultdict(list)
for item in lst:
    if item['passed']:
        info[item['task_id']].append(item['output'])
len(info)

349

In [495]:
lst = read_jsonl('LeetCodeDataset-v0.3.1.jsonl')
show_list(lst)

List length: 2869


{'task_id': 'two-sum',
 'question_id': 1,
 'difficulty': 'Easy',
 'tags': ['Array', 'Hash Table'],
 'problem_description': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?',
 'starter_code': 'class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n  

In [496]:
result = []
for item in lst:
    task_id = item['task_id']
    if task_id in info:
        assert not item['response']
        item['response'] = random.choice(info[task_id])
        result.append(item)
show_list(result)

List length: 349


{'task_id': 'longest-palindromic-substring',
 'question_id': 5,
 'difficulty': 'Medium',
 'tags': ['Two Pointers', 'String', 'Dynamic Programming'],
 'problem_description': 'Given a string s, return the longest palindromic substring in s.\n\xa0\nExample 1:\n\nInput: s = "babad"\nOutput: "bab"\nExplanation: "aba" is also a valid answer.\n\nExample 2:\n\nInput: s = "cbbd"\nOutput: "bb"\n\n\xa0\nConstraints:\n\n1 <= s.length <= 1000\ns consist of only digits and English letters.\n\n',
 'starter_code': 'class Solution:\n    def longestPalindrome(self, s: str) -> str:\n        ',
 'estimated_date': '2015-08-07',
 'prompt': "import random\nimport functools\nimport collections\nimport string\nimport math\nimport datetime\n\nfrom typing import *\nfrom functools import *\nfrom collections import *\nfrom itertools import *\nfrom heapq import *\nfrom bisect import *\nfrom string import *\nfrom operator import *\nfrom math import *\n\ninf = float('inf')\n\nclass ListNode:\n    def __init__(self, v

In [499]:
write_jsonl('LeetCodeDataset-v0.3.1-2845-response.jsonl', lst)

In [501]:
r = [item for item in lst if not item['response']]
write_jsonl('leetcode-2869-unsolve-24-problems.jsonl', r)

In [502]:
s = set(item['task_id'] for item in r)
len(s)

24

In [503]:
lst = read_jsonl('vllm_predict-373-32b-100-times.jsonl')
result = [item for item in lst if item['task_id'] in s]
show_list(result)

List length: 2400


{'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nGiven the root of a complete binary tree, return the number of the nodes in the tree.\nAccording to Wikipedia, every level, except possibly the last, is completely filled in a complete binary tree, and all nodes in the last level are as far left as possible. It can have between 1 and 2h nodes inclusive at the last level h.\nDesign an algorithm that runs in less than\xa0O(n)\xa0time complexity.\n\xa0\nExample 1:\n\n\nInput: root = [1,2,3,4,5,6]\nOutput: 6\n\nExample 2:\n\nInput: root = []\nOutput: 0\n\nExample 3:\n\nInput: root = [1]\nOutput: 1\n\n\xa0\nConstraints:\n\nThe number of nodes in the tree is in the range [0, 5 * 104].\n0 <= Node.val <= 5 * 104\nThe tree is guaranteed to be complete.\n\n\n\n### Format: You will use the following starter code to write the solution t

In [504]:
write_jsonl('vllm_predict-24-32b-100-times.jsonl', result)

In [505]:
lst = read_jsonl('vllm_predict-24-32b-100-times.jsonl_results.jsonl')
show_list(lst)

List length: 2400


{'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nGiven the root of a complete binary tree, return the number of the nodes in the tree.\nAccording to Wikipedia, every level, except possibly the last, is completely filled in a complete binary tree, and all nodes in the last level are as far left as possible. It can have between 1 and 2h nodes inclusive at the last level h.\nDesign an algorithm that runs in less than\xa0O(n)\xa0time complexity.\n\xa0\nExample 1:\n\n\nInput: root = [1,2,3,4,5,6]\nOutput: 6\n\nExample 2:\n\nInput: root = []\nOutput: 0\n\nExample 3:\n\nInput: root = [1]\nOutput: 1\n\n\xa0\nConstraints:\n\nThe number of nodes in the tree is in the range [0, 5 * 104].\n0 <= Node.val <= 5 * 104\nThe tree is guaranteed to be complete.\n\n\n\n### Format: You will use the following starter code to write the solution t

In [506]:
src2tgt = {item['query']: item['output'] for item in lst if item['passed'] if item['passed']}
len(src2tgt)

14

In [507]:
l = [item for item in read_jsonl('vllm_predict-24-32b-100-times.jsonl') if item['query'] not in src2tgt]
show_list(l)

List length: 1000


{'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nGiven the root of a complete binary tree, return the number of the nodes in the tree.\nAccording to Wikipedia, every level, except possibly the last, is completely filled in a complete binary tree, and all nodes in the last level are as far left as possible. It can have between 1 and 2h nodes inclusive at the last level h.\nDesign an algorithm that runs in less than\xa0O(n)\xa0time complexity.\n\xa0\nExample 1:\n\n\nInput: root = [1,2,3,4,5,6]\nOutput: 6\n\nExample 2:\n\nInput: root = []\nOutput: 0\n\nExample 3:\n\nInput: root = [1]\nOutput: 1\n\n\xa0\nConstraints:\n\nThe number of nodes in the tree is in the range [0, 5 * 104].\n0 <= Node.val <= 5 * 104\nThe tree is guaranteed to be complete.\n\n\n\n### Format: You will use the following starter code to write the solution t

In [508]:
write_jsonl('vllm_predict-10-32b-100-times.jsonl', l)

In [509]:
for i, item in enumerate(l[: 10]):
    print(i)
    print(item['query'], '\n\n\n\n')

0
You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.

### Question:
Given the root of a complete binary tree, return the number of the nodes in the tree.
According to Wikipedia, every level, except possibly the last, is completely filled in a complete binary tree, and all nodes in the last level are as far left as possible. It can have between 1 and 2h nodes inclusive at the last level h.
Design an algorithm that runs in less than O(n) time complexity.
 
Example 1:


Input: root = [1,2,3,4,5,6]
Output: 6

Example 2:

Input: root = []
Output: 0

Example 3:

Input: root = [1]
Output: 1

 
Constraints:

The number of nodes in the tree is in the range [0, 5 * 104].
0 <= Node.val <= 5 * 104
The tree is guaranteed to be complete.



### Format: You will use the following starter code to write the solution to the problem and enclose your code within delimiters

In [510]:
lst = read_jsonl('LeetCodeDataset-v0.3.1.jsonl')
show_list(lst)

List length: 2869


{'task_id': 'two-sum',
 'question_id': 1,
 'difficulty': 'Easy',
 'tags': ['Array', 'Hash Table'],
 'problem_description': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?',
 'starter_code': 'class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n  

In [511]:
count = defaultdict(int)
for item in lst:
    count[item['difficulty']] += 1
count

defaultdict(int, {'Easy': 686, 'Medium': 1498, 'Hard': 685})

In [513]:
686 / 2869, 1498 / 2869, 685 / 2869

(0.23910770303241546, 0.5221331474381318, 0.23875914952945276)

In [531]:
filename = 'vllm_predict-qwq-10.jsonl'
lst1 = read_jsonl('vllm_predict-32b-2869-10-500-times-part1.jsonl')
lst2 = read_jsonl(filename)
show_list(lst1)
show_list(lst2)
cnt = 0
for a, b in zip(lst1, lst2):
    assert a['query'] == b['query']
    b['task_id'] = a['task_id']
    if '</think>' in b['output']:
        tgt = b['output'].split('</think>', 1)[1]
        cnt += 1
    else:
        tgt = b['output']
    b['completion'] = extract_completion(tgt)
write_jsonl(filename=filename, data=lst2)
show_list(lst2)

List length: 1000
List length: 1000
List length: 1000


{'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nGiven the root of a complete binary tree, return the number of the nodes in the tree.\nAccording to Wikipedia, every level, except possibly the last, is completely filled in a complete binary tree, and all nodes in the last level are as far left as possible. It can have between 1 and 2h nodes inclusive at the last level h.\nDesign an algorithm that runs in less than\xa0O(n)\xa0time complexity.\n\xa0\nExample 1:\n\n\nInput: root = [1,2,3,4,5,6]\nOutput: 6\n\nExample 2:\n\nInput: root = []\nOutput: 0\n\nExample 3:\n\nInput: root = [1]\nOutput: 1\n\n\xa0\nConstraints:\n\nThe number of nodes in the tree is in the range [0, 5 * 104].\n0 <= Node.val <= 5 * 104\nThe tree is guaranteed to be complete.\n\n\n\n### Format: You will use the following starter code to write the solution t

In [542]:
lst1 = read_jsonl('vllm_predict-24-32b-100-times.jsonl_results.jsonl')
lst2 = read_jsonl('vllm_predict-32b-2869-10-500-times.jsonl_results.jsonl')
show_list(lst1)
show_list(lst2)

List length: 2400
List length: 5000


{'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nGiven the root of a complete binary tree, return the number of the nodes in the tree.\nAccording to Wikipedia, every level, except possibly the last, is completely filled in a complete binary tree, and all nodes in the last level are as far left as possible. It can have between 1 and 2h nodes inclusive at the last level h.\nDesign an algorithm that runs in less than\xa0O(n)\xa0time complexity.\n\xa0\nExample 1:\n\n\nInput: root = [1,2,3,4,5,6]\nOutput: 6\n\nExample 2:\n\nInput: root = []\nOutput: 0\n\nExample 3:\n\nInput: root = [1]\nOutput: 1\n\n\xa0\nConstraints:\n\nThe number of nodes in the tree is in the range [0, 5 * 104].\n0 <= Node.val <= 5 * 104\nThe tree is guaranteed to be complete.\n\n\n\n### Format: You will use the following starter code to write the solution t

In [543]:
id2tgt = {item['task_id']: item['output'] for item in lst1+lst2 if item['passed']}
len(id2tgt)

17

In [544]:
lst = read_jsonl('LeetCodeDataset-v0.3.1-2845-response.jsonl')
show_list(lst)

List length: 2869


{'task_id': 'two-sum',
 'question_id': 1,
 'difficulty': 'Easy',
 'tags': ['Array', 'Hash Table'],
 'problem_description': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?',
 'starter_code': 'class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n  

In [545]:
cnt = 0
for item in lst:
    if item['task_id'] in id2tgt:
        assert not item['response']
        item['response'] = id2tgt[item['task_id']]
        cnt += 1
cnt

17

In [546]:
write_jsonl('LeetCodeDataset-v0.3.1-2862-response.jsonl', lst)

In [549]:
lst = read_jsonl('LeetCodeDataset-v0.3.1-2862-response.jsonl')

In [550]:
cnt = 0
for item in lst:
    if not item['response']:
        item['response'] = "```python\n" + item['completion'] + '\n```'
        # print(item['response'], '\n\n\n\n')
        cnt += 1
cnt

7

In [551]:
for item in lst:
    assert '```python' in item['response']

In [552]:
write_jsonl('LeetCodeDataset-v0.3.1.jsonl', lst)

In [553]:
lst = read_jsonl('LeetCodeDataset-v0.3.1.jsonl')
show_list(lst)

List length: 2869


{'task_id': 'two-sum',
 'question_id': 1,
 'difficulty': 'Easy',
 'tags': ['Array', 'Hash Table'],
 'problem_description': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?',
 'starter_code': 'class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n  

In [555]:
result = []
for item in lst:
    if item['estimated_date'] < '2024-07-01':
        src = item['query']
        tgt = item['response']
        result.append({
            'instruction': src,
            'input': '',
            'output': tgt,
            'task_id': item['task_id'],
            'question_id': item['question_id']
        })
random.shuffle(result)
show_list(result)

List length: 2613


{'instruction': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nYou are given a 0-indexed 2D integer array pairs where pairs[i] = [starti, endi]. An arrangement of pairs is valid if for every index i where 1 <= i < pairs.length, we have endi-1 == starti.\nReturn any valid arrangement of pairs.\nNote: The inputs will be generated such that there exists a valid arrangement of pairs.\n\xa0\nExample 1:\n\nInput: pairs = [[5,1],[4,5],[11,9],[9,4]]\nOutput: [[11,9],[9,4],[4,5],[5,1]]\nExplanation:\nThis is a valid arrangement since endi-1 always equals starti.\nend0 = 9 == 9 = start1 \nend1 = 4 == 4 = start2\nend2 = 5 == 5 = start3\n\nExample 2:\n\nInput: pairs = [[1,3],[3,2],[2,1]]\nOutput: [[1,3],[3,2],[2,1]]\nExplanation:\nThis is a valid arrangement since endi-1 always equals starti.\nend0 = 3 == 3 = start1\nend1 = 2 == 2 = start2\nT

In [556]:
write_jsonl('leetcode-v031-train-llama.jsonl', result)

In [558]:
result = []
for item in lst:
    if item['estimated_date'] < '2024-07-01':
        src = item['query']
        tgt = item['completion']
        result.append({
            'instruction': src,
            'input': '',
            'output': '```python\n' + tgt + '\n```',
            'task_id': item['task_id'],
            'question_id': item['question_id']
        })
random.shuffle(result)
show_list(result)

List length: 2613


{'instruction': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nThere is a new alien language that uses the English alphabet. However, the order of the letters is unknown to you.\nYou are given a list of strings words from the alien language\'s dictionary. Now it is claimed that the strings in words are sorted lexicographically by the rules of this new language.\nIf this claim is incorrect, and the given arrangement of string in\xa0words\xa0cannot correspond to any order of letters,\xa0return\xa0"".\nOtherwise, return a string of the unique letters in the new alien language sorted in lexicographically increasing order by the new language\'s rules. If there are multiple solutions, return any of them.\n\xa0\nExample 1:\n\nInput: words = ["wrt","wrf","er","ett","rftt"]\nOutput: "wertf"\n\nExample 2:\n\nInput: words = ["z","x"]\nOutput

In [560]:
print(result[0]['output'])

```python
class Solution:
    def alienOrder(self, words: List[str]) -> str:
        g = [[False] * 26 for _ in range(26)]
        s = [False] * 26
        cnt = 0
        n = len(words)
        for i in range(n - 1):
            for c in words[i]:
                if cnt == 26:
                    break
                o = ord(c) - ord('a')
                if not s[o]:
                    cnt += 1
                    s[o] = True
            m = len(words[i])
            for j in range(m):
                if j >= len(words[i + 1]):
                    return ''
                c1, c2 = words[i][j], words[i + 1][j]
                if c1 == c2:
                    continue
                o1, o2 = ord(c1) - ord('a'), ord(c2) - ord('a')
                if g[o2][o1]:
                    return ''
                g[o1][o2] = True
                break
        for c in words[n - 1]:
            if cnt == 26:
                break
            o = ord(c) - ord('a')
            if not s[o]:
    

In [561]:
write_jsonl('leetcode-v031-train-human-llama.jsonl', result)

In [590]:
lst1 = read_jsonl('LeetCodeDataset-v0.3.1-test_qwq-plus_20250405_135348_results.jsonl_results.jsonl')
lst2 = read_jsonl('LeetCodeDataset-v0.3.1-test.jsonl')
show_list(lst1)
show_list(lst2)
info = {tag: [0, 0, 0] for item in lst2 for tag in item['tags']}
info['all'] = [0, 0, 0]
for a, b in zip(lst1, lst2):
    a['query'] == b['query']
    # for tag in b['tags'] + ['all']:
    #     info[tag][0] += 1
    #     info[tag][1] += int(a['passed'])
    if b['difficulty'] == 'Easy':
        index = 0
    elif b['difficulty'] == 'Medium':
        index = 1
    else:
        assert b['difficulty'] == 'Hard'
        index = 2
    for tag in b['tags'] + ['all']:
        info[tag][index] += 1

for k, v in sorted(info.items(), key=lambda x: sum(x[1]), reverse=True):
    # print(k, round(v[1]/v[0] * 100, 1))
    print(k, v)

List length: 256
List length: 256
all [54, 116, 86]
Array [32, 83, 53]
String [14, 27, 26]
Dynamic Programming [0, 25, 32]
Hash Table [11, 27, 18]
Math [16, 15, 24]
Greedy [3, 20, 9]
Sorting [2, 22, 6]
Prefix Sum [4, 12, 12]
Binary Search [1, 13, 12]
Sliding Window [4, 12, 7]
Enumeration [3, 9, 10]
Matrix [2, 11, 8]
Simulation [10, 7, 2]
Depth-First Search [0, 10, 9]
Bit Manipulation [4, 7, 7]
Combinatorics [1, 2, 13]
Counting [4, 6, 5]
Graph [0, 10, 5]
Heap (Priority Queue) [2, 11, 2]
Number Theory [2, 4, 7]
Breadth-First Search [0, 8, 4]
Tree [0, 4, 7]
Two Pointers [0, 8, 2]
Segment Tree [1, 3, 6]
String Matching [1, 1, 4]
Stack [0, 2, 3]
Shortest Path [0, 5, 0]
Backtracking [0, 3, 1]
Monotonic Stack [0, 1, 3]
Union Find [0, 1, 3]
Bitmask [0, 1, 3]
Game Theory [1, 1, 1]
Geometry [0, 1, 2]
Trie [1, 1, 1]
Hash Function [0, 1, 2]
Recursion [2, 0, 1]
Topological Sort [0, 1, 2]
Ordered Set [0, 1, 1]
Rolling Hash [0, 1, 1]
Binary Indexed Tree [0, 1, 1]
Suffix Array [0, 0, 1]
Linked List [0

In [572]:
lst2[0]

{'task_id': 'find-the-encrypted-string',
 'question_id': 3210,
 'difficulty': 'Easy',
 'tags': ['String'],
 'problem_description': 'You are given a string s and an integer k. Encrypt the string using the following algorithm:\n\nFor each character c in s, replace c with the kth character after c in the string (in a cyclic manner).\n\nReturn the encrypted string.\n\xa0\nExample 1:\n\nInput: s = "dart", k = 3\nOutput: "tdar"\nExplanation:\n\nFor i = 0, the 3rd character after \'d\' is \'t\'.\nFor i = 1, the 3rd character after \'a\' is \'d\'.\nFor i = 2, the 3rd character after \'r\' is \'a\'.\nFor i = 3, the 3rd character after \'t\' is \'r\'.\n\n\nExample 2:\n\nInput: s = "aaa", k = 1\nOutput: "aaa"\nExplanation:\nAs all the characters are the same, the encrypted string will also be the same.\n\n\xa0\nConstraints:\n\n1 <= s.length <= 100\n1 <= k <= 104\ns consists only of lowercase English letters.\n\n',
 'starter_code': 'class Solution:\n    def getEncryptedString(self, s: str, k: int)

In [598]:
file = 'vllm_predict-256-open-thought.jsonl'
lst1 = read_jsonl('LeetCodeDataset-v0.3.1-test.jsonl')
lst2 = read_jsonl(file)
for a, b in zip(lst1, lst2):
    assert a['query'] == b['query']
    b['task_id'] = a['task_id']
    b['completion'] = extract_completion(b['output'])
write_jsonl(file, lst2)
show_list(lst2)

List length: 256


{'query': 'You are an expert Python programmer. You will be given a question (problem specification) and will generate a correct Python program that matches the specification and passes all tests.\n\n### Question:\nYou are given a string s and an integer k. Encrypt the string using the following algorithm:\n\nFor each character c in s, replace c with the kth character after c in the string (in a cyclic manner).\n\nReturn the encrypted string.\n\xa0\nExample 1:\n\nInput: s = "dart", k = 3\nOutput: "tdar"\nExplanation:\n\nFor i = 0, the 3rd character after \'d\' is \'t\'.\nFor i = 1, the 3rd character after \'a\' is \'d\'.\nFor i = 2, the 3rd character after \'r\' is \'a\'.\nFor i = 3, the 3rd character after \'t\' is \'r\'.\n\n\nExample 2:\n\nInput: s = "aaa", k = 1\nOutput: "aaa"\nExplanation:\nAs all the characters are the same, the encrypted string will also be the same.\n\n\xa0\nConstraints:\n\n1 <= s.length <= 100\n1 <= k <= 104\ns consists only of lowercase English letters.\n\n\n\

In [3]:
from utils import *

lst = read_jsonl('leetcode-2869-5-times-EB_SPV4_32K_DNI_V45T_code_sft_v0.0.8_8800_0411.jsonl_results.jsonl')
show_list(lst)

14345
dict_keys(['task_id', 'query', 'date', 'tgt', 'completion', 'result', 'passed'])
{'task_id': 'two-sum', 'query': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?\n\nPlease solve the problem with the following starter code:\n```python\nclass Solution:\n    def twoSum(self

In [6]:
id2query = {item['task_id']: item['query'] for item in lst if item['tgt'] and not item['passed'] and item['date'] < '2024-08-01'}
len(id2query)

1046

In [8]:
r = list(id2query.items())
show_list(r)

1046
('two-sum', 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?\n\nPlease solve the problem with the following starter code:\n```python\nclass Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n        \n```')


In [9]:
result = []
for _ in range(5):
    for k, v in r:
        result.append({
            'task_id': k,
            'query': v
        })
show_list(result)

5230
dict_keys(['task_id', 'query'])
{'task_id': 'two-sum', 'query': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?\n\nPlease solve the problem with the following starter code:\n```python\nclass Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n   

In [10]:
write_jsonl('leetcode-v031-rl-before-2024-08-01-5-times.jsonl', result)

In [13]:
result[1]

{'task_id': 'longest-palindromic-substring',
 'query': 'Given a string s, return the longest palindromic substring in s.\n\xa0\nExample 1:\n\nInput: s = "babad"\nOutput: "bab"\nExplanation: "aba" is also a valid answer.\n\nExample 2:\n\nInput: s = "cbbd"\nOutput: "bb"\n\n\xa0\nConstraints:\n\n1 <= s.length <= 1000\ns consist of only digits and English letters.\n\n\n\nPlease solve the problem with the following starter code:\n```python\nclass Solution:\n    def longestPalindrome(self, s: str) -> str:\n        \n```'}

In [14]:
lst = read_jsonl('leetcode-2869-5-times-EB_SPV4_32K_DNI_V45T_code_sft_v0.0.8_8800_0411.jsonl_results.jsonl')
show_list(lst)

14345
dict_keys(['task_id', 'query', 'date', 'tgt', 'completion', 'result', 'passed'])
{'task_id': 'two-sum', 'query': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?\n\nPlease solve the problem with the following starter code:\n```python\nclass Solution:\n    def twoSum(self

In [20]:
info = dict()
for item in lst:
    if item['date'] < '2024-08-01':
        src = item['query']
        tgt = item['tgt']
        if src not in info:
            info[src] = {'chosen': [], 'rejected': []}
        if item['passed']:
            info[src]['chosen'].append(tgt)
        else:
            info[src]['rejected'].append(tgt)
len(info)

2641

In [21]:
import random

result = []
for src, v in info.items():
    if v['chosen'] and v['rejected']:
        chosen = random.choice(v['chosen'])
        rejected = random.choice(v['rejected'])
        result.append({
            'instruction': src,
            'input': '',
            'output': [chosen, rejected],
            'model_id': 'EB_SPV4_32K_DNI_V45T_code_sft_v0.0.8_8800_0411'
        })
show_list(result)

622
dict_keys(['instruction', 'input', 'output', 'model_id'])
{'instruction': 'The string "PAYPALISHIRING" is written in a zigzag pattern on a given number of rows like this: (you may want to display this pattern in a fixed font for better legibility)\n\nP   A   H   N\nA P L S I I G\nY   I   R\n\nAnd then read line by line: "PAHNAPLSIIGYIR"\nWrite the code that will take a string and make this conversion given a number of rows:\n\nstring convert(string s, int numRows);\n\n\xa0\nExample 1:\n\nInput: s = "PAYPALISHIRING", numRows = 3\nOutput: "PAHNAPLSIIGYIR"\n\nExample 2:\n\nInput: s = "PAYPALISHIRING", numRows = 4\nOutput: "PINALSIGYAHRPI"\nExplanation:\nP     I    N\nA   L S  I G\nY A   H R\nP     I\n\nExample 3:\n\nInput: s = "A", numRows = 1\nOutput: "A"\n\n\xa0\nConstraints:\n\n1 <= s.length <= 1000\ns consists of English letters (lower-case and upper-case), \',\' and \'.\'.\n1 <= numRows <= 1000\n\n\n\nPlease solve the problem with the following starter code:\n```python\nclass Sol

In [22]:
write_jsonl('dpo-0412-leetcode-result-llama.jsonl', result)

In [9]:
lst = read_jsonl('leetcode-2869-5-times-EB_SPV4_32K_DNI_V45T_code_sft_v0.0.8_8800_0411.jsonl_results.jsonl')
show_list(lst)

14345
dict_keys(['task_id', 'query', 'date', 'tgt', 'completion', 'result', 'passed'])
{'task_id': 'two-sum', 'query': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?\n\nPlease solve the problem with the following starter code:\n```python\nclass Solution:\n    def twoSum(self

In [13]:
import random

info = dict()
for item in lst:
    src = item['query']
    thought = item['tgt']
    tgt = item['tgt']
    if thought and tgt:
        if src not in info:
            info[src] = {'chosen': [], 'rejected': []}
        if item['passed']:
            info[src]['chosen'].append((thought, tgt))
        else:
            info[src]['rejected'].append((thought, tgt))
result = []
for src, v in info.items():
    if v['chosen'] and v['rejected']:
        chosen = random.choice(v['chosen'])
        rejected = random.choice(v['rejected'])
        result.append({
            'instruction': src,
            'input': '',
            'output': [chosen[1], rejected[1]],
            'thought': [chosen[0], rejected[0]],
        })
show_list(result)

611
dict_keys(['instruction', 'input', 'output', 'thought'])
{'instruction': 'Given an integer x, return true if x is a palindrome, and false otherwise.\n\xa0\nExample 1:\n\nInput: x = 121\nOutput: true\nExplanation: 121 reads as 121 from left to right and from right to left.\n\nExample 2:\n\nInput: x = -121\nOutput: false\nExplanation: From left to right, it reads -121. From right to left, it becomes 121-. Therefore it is not a palindrome.\n\nExample 3:\n\nInput: x = 10\nOutput: false\nExplanation: Reads 01 from right to left. Therefore it is not a palindrome.\n\n\xa0\nConstraints:\n\n-231\xa0<= x <= 231\xa0- 1\n\n\xa0\nFollow up: Could you solve it without converting the integer to a string?\n\nPlease solve the problem with the following starter code:\n```python\nclass Solution:\n    def isPalindrome(self, x: int) -> bool:\n        \n```', 'input': '', 'output': ['Given an integer x, return true if x is a palindrome, and false otherwise.\n\xa0\nExample 1:\n\nInput: x = 121\nOutput: t

In [15]:
sum(1 for v in info.values() if not v['chosen'] and v['rejected'])

618

In [30]:
write_jsonl('dpo-0412-leetcode-10090-eval-result.jsonl', result)

In [2]:
from utils import *

lst = read_jsonl('LeetCodeDataset-v0.3.1.jsonl')
show_list(lst)

2869
dict_keys(['task_id', 'question_id', 'difficulty', 'tags', 'problem_description', 'starter_code', 'estimated_date', 'prompt', 'completion', 'entry_point', 'test', 'input_output', 'query', 'response'])
{'task_id': 'two-sum', 'question_id': 1, 'difficulty': 'Easy', 'tags': ['Array', 'Hash Table'], 'problem_description': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\

In [3]:
lst[0]

{'task_id': 'two-sum',
 'question_id': 1,
 'difficulty': 'Easy',
 'tags': ['Array', 'Hash Table'],
 'problem_description': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?',
 'starter_code': 'class Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n  

In [4]:
result = [item for item in lst if item['estimated_date'] < '2024-08-01']
show_list(result)

2641
dict_keys(['task_id', 'question_id', 'difficulty', 'tags', 'problem_description', 'starter_code', 'estimated_date', 'prompt', 'completion', 'entry_point', 'test', 'input_output', 'query', 'response'])
{'task_id': 'two-sum', 'question_id': 1, 'difficulty': 'Easy', 'tags': ['Array', 'Hash Table'], 'problem_description': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\

In [5]:
write_jsonl('LeetCodeDataset-v0.3.1-train.jsonl', result)

In [8]:
result = [item for item in lst if item['estimated_date'] >= '2024-08-01']
write_jsonl('LeetCodeDataset-v0.3.1-test.jsonl', result)
show_list(result)

228
dict_keys(['task_id', 'question_id', 'difficulty', 'tags', 'problem_description', 'starter_code', 'estimated_date', 'prompt', 'completion', 'entry_point', 'test', 'input_output', 'query', 'response'])
{'task_id': 'shortest-distance-after-road-addition-queries-i', 'question_id': 3243, 'difficulty': 'Medium', 'tags': ['Breadth-First Search', 'Graph', 'Array'], 'problem_description': 'You are given an integer n and a 2D integer array queries.\nThere are n cities numbered from 0 to n - 1. Initially, there is a unidirectional road from city i to city i + 1 for all 0 <= i < n - 1.\nqueries[i] = [ui, vi] represents the addition of a new unidirectional road from city ui to city vi. After each query, you need to find the length of the shortest path from city 0 to city n - 1.\nReturn an array answer where for each i in the range [0, queries.length - 1], answer[i] is the length of the shortest path from city 0 to city n - 1 after processing the first i + 1 queries.\n\xa0\nExample 1:\n\nInput:

In [16]:
lst = read_jsonl('leetcode-1046-5-times-0413.jsonl')
show_list(lst)

5230
dict_keys(['task_id', 'query', 'idx', 'output', 'model_id', 'temperature', 'topp', 'completion'])
{'task_id': 'permutations', 'query': 'Given an array nums of distinct integers, return all the possible permutations. You can return the answer in any order.\n\xa0\nExample 1:\nInput: nums = [1,2,3]\nOutput: [[1,2,3],[1,3,2],[2,1,3],[2,3,1],[3,1,2],[3,2,1]]\nExample 2:\nInput: nums = [0,1]\nOutput: [[0,1],[1,0]]\nExample 3:\nInput: nums = [1]\nOutput: [[1]]\n\n\xa0\nConstraints:\n\n1 <= nums.length <= 6\n-10 <= nums[i] <= 10\nAll the integers of nums are unique.\n\n\n\nPlease solve the problem with the following starter code:\n```python\nclass Solution:\n    def permute(self, nums: List[int]) -> List[List[int]]:\n        \n```', 'idx': 96683, 'output': "To solve this problem, we need to generate all possible permutations of a given array of distinct integers. A permutation is an arrangement of all or part of a set of objects, with regard to the order of the arrangement. Since all inte

In [17]:
s = set(item['task_id'] for item in lst)

In [18]:
lst = read_jsonl('LeetCodeDataset-v0.3.1.jsonl')
show_list(lst)

2869
dict_keys(['task_id', 'question_id', 'difficulty', 'tags', 'problem_description', 'starter_code', 'estimated_date', 'prompt', 'completion', 'entry_point', 'test', 'input_output', 'query', 'response'])
{'task_id': 'two-sum', 'question_id': 1, 'difficulty': 'Easy', 'tags': ['Array', 'Hash Table'], 'problem_description': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\

In [20]:
result = []
for item in lst:
    if item['task_id'] in s:
        assert item['estimated_date'] < '2024-08-01'
        result.append(item)
show_list(result)
write_jsonl('LeetCodeDataset-v0.3.1-1046.jsonl', result)


1046
dict_keys(['task_id', 'question_id', 'difficulty', 'tags', 'problem_description', 'starter_code', 'estimated_date', 'prompt', 'completion', 'entry_point', 'test', 'input_output', 'query', 'response'])
{'task_id': 'two-sum', 'question_id': 1, 'difficulty': 'Easy', 'tags': ['Array', 'Hash Table'], 'problem_description': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\

In [21]:
lst = read_jsonl('leetcode-1046-5-times-0413.jsonl_results.jsonl')
show_list(lst)

5230
dict_keys(['task_id', 'query', 'idx', 'output', 'model_id', 'temperature', 'topp', 'completion', 'result', 'passed'])
{'task_id': 'permutations', 'query': 'Given an array nums of distinct integers, return all the possible permutations. You can return the answer in any order.\n\xa0\nExample 1:\nInput: nums = [1,2,3]\nOutput: [[1,2,3],[1,3,2],[2,1,3],[2,3,1],[3,1,2],[3,2,1]]\nExample 2:\nInput: nums = [0,1]\nOutput: [[0,1],[1,0]]\nExample 3:\nInput: nums = [1]\nOutput: [[1]]\n\n\xa0\nConstraints:\n\n1 <= nums.length <= 6\n-10 <= nums[i] <= 10\nAll the integers of nums are unique.\n\n\n\nPlease solve the problem with the following starter code:\n```python\nclass Solution:\n    def permute(self, nums: List[int]) -> List[List[int]]:\n        \n```', 'idx': 96683, 'output': "To solve this problem, we need to generate all possible permutations of a given array of distinct integers. A permutation is an arrangement of all or part of a set of objects, with regard to the order of the arrange

In [22]:
lst[0]

{'task_id': 'permutations',
 'query': 'Given an array nums of distinct integers, return all the possible permutations. You can return the answer in any order.\n\xa0\nExample 1:\nInput: nums = [1,2,3]\nOutput: [[1,2,3],[1,3,2],[2,1,3],[2,3,1],[3,1,2],[3,2,1]]\nExample 2:\nInput: nums = [0,1]\nOutput: [[0,1],[1,0]]\nExample 3:\nInput: nums = [1]\nOutput: [[1]]\n\n\xa0\nConstraints:\n\n1 <= nums.length <= 6\n-10 <= nums[i] <= 10\nAll the integers of nums are unique.\n\n\n\nPlease solve the problem with the following starter code:\n```python\nclass Solution:\n    def permute(self, nums: List[int]) -> List[List[int]]:\n        \n```',
 'idx': 96683,
 'output': "To solve this problem, we need to generate all possible permutations of a given array of distinct integers. A permutation is an arrangement of all or part of a set of objects, with regard to the order of the arrangement. Since all integers in the array are distinct, each permutation will be a unique arrangement of these integers.\n\n

In [23]:
from tqdm import tqdm
import random

info = dict()
for item in tqdm(lst):
    if item and item['output']:
        src = item['query']
        tgt = item['output']
        if src not in info:
            info[src] = {'chosen': [], 'rejected': []}
        if item['passed']:
            info[src]['chosen'].append(tgt)
        else:
            info[src]['rejected'].append(tgt)
print(len(info))
result = []
for k, v in info.items():
    if v['chosen'] and v['rejected']:
        chosen = random.choice(v['chosen'])
        rejected = random.choice(v['rejected'])
        result.append({
            'instruction': k,
            'input': '',
            'output': [chosen, rejected]
        })
show_list(result)

100%|██████████| 5230/5230 [00:00<00:00, 241646.76it/s]

1046
371
dict_keys(['instruction', 'input', 'output'])
{'instruction': 'Given an array nums of distinct integers, return all the possible permutations. You can return the answer in any order.\n\xa0\nExample 1:\nInput: nums = [1,2,3]\nOutput: [[1,2,3],[1,3,2],[2,1,3],[2,3,1],[3,1,2],[3,2,1]]\nExample 2:\nInput: nums = [0,1]\nOutput: [[0,1],[1,0]]\nExample 3:\nInput: nums = [1]\nOutput: [[1]]\n\n\xa0\nConstraints:\n\n1 <= nums.length <= 6\n-10 <= nums[i] <= 10\nAll the integers of nums are unique.\n\n\n\nPlease solve the problem with the following starter code:\n```python\nclass Solution:\n    def permute(self, nums: List[int]) -> List[List[int]]:\n        \n```', 'input': '', 'output': ["To solve this problem, we need to generate all possible permutations of a given array of distinct integers. The solution involves exploring all possible arrangements of the elements in the array through backtracking or recursive methods.\n\n### Approach\n1. **Backtracking**: The key idea is to fix one e

In [24]:
write_jsonl('leetcode-1046-0413-dpo-llama.jsonl', result)

In [29]:
lst = read_jsonl('leetcode-1046-5-times-0413-think-fix.jsonl_results.jsonl')
show_list(lst)

5230
dict_keys(['task_id', 'query', 'output', 'completion', 'result', 'passed'])
{'task_id': 'two-sum', 'query': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?\n\nPlease solve the problem with the following starter code:\n```python\nclass Solution:\n    def twoSum(self, nums

In [26]:
lst[0]

{'task_id': 'two-sum',
 'query': 'Given an array of integers nums\xa0and an integer target, return indices of the two numbers such that they add up to target.\nYou may assume that each input would have exactly one solution, and you may not use the same element twice.\nYou can return the answer in any order.\n\xa0\nExample 1:\n\nInput: nums = [2,7,11,15], target = 9\nOutput: [0,1]\nExplanation: Because nums[0] + nums[1] == 9, we return [0, 1].\n\nExample 2:\n\nInput: nums = [3,2,4], target = 6\nOutput: [1,2]\n\nExample 3:\n\nInput: nums = [3,3], target = 6\nOutput: [0,1]\n\n\xa0\nConstraints:\n\n2 <= nums.length <= 104\n-109 <= nums[i] <= 109\n-109 <= target <= 109\nOnly one valid answer exists.\n\n\xa0\nFollow-up:\xa0Can you come up with an algorithm that is less than O(n2)\xa0time complexity?\n\nPlease solve the problem with the following starter code:\n```python\nclass Solution:\n    def twoSum(self, nums: List[int], target: int) -> List[int]:\n        \n```',
 'output': "Okay, I nee

In [30]:
import random

info = dict()
for item in lst:
    src = item['query']
    splits = item['output'].split('<mask:9>')
    if len(splits) == 2:
        thought, tgt = splits
        if thought and tgt:
            if src not in info:
                info[src] = {'chosen': [], 'rejected': []}
            if item['passed']:
                info[src]['chosen'].append((thought, tgt))
            else:
                info[src]['rejected'].append((thought, tgt))
result = []
for src, v in info.items():
    if v['chosen'] and v['rejected']:
        chosen = random.choice(v['chosen'])
        rejected = random.choice(v['rejected'])
        result.append({
            'instruction': src,
            'input': '',
            'output': [chosen[1], rejected[1]],
            'thought': [chosen[0], rejected[0]],
        })
show_list(result)

343
dict_keys(['instruction', 'input', 'output', 'thought'])
{'instruction': 'You are given a string s and an array of strings words. All the strings of words are of the same length.\nA concatenated string is a string that exactly contains all the strings of any permutation of words concatenated.\n\nFor example, if words = ["ab","cd","ef"], then "abcdef", "abefcd", "cdabef", "cdefab", "efabcd", and "efcdab" are all concatenated strings. "acdbef" is not a concatenated string because it is not the concatenation of any permutation of words.\n\nReturn an array of the starting indices of all the concatenated substrings in s. You can return the answer in any order.\n\xa0\nExample 1:\n\nInput: s = "barfoothefoobarman", words = ["foo","bar"]\nOutput: [0,9]\nExplanation:\nThe substring starting at 0 is "barfoo". It is the concatenation of ["bar","foo"] which is a permutation of words.\nThe substring starting at 9 is "foobar". It is the concatenation of ["foo","bar"] which is a permutation of wo

In [31]:
result[0]

{'instruction': 'You are given a string s and an array of strings words. All the strings of words are of the same length.\nA concatenated string is a string that exactly contains all the strings of any permutation of words concatenated.\n\nFor example, if words = ["ab","cd","ef"], then "abcdef", "abefcd", "cdabef", "cdefab", "efabcd", and "efcdab" are all concatenated strings. "acdbef" is not a concatenated string because it is not the concatenation of any permutation of words.\n\nReturn an array of the starting indices of all the concatenated substrings in s. You can return the answer in any order.\n\xa0\nExample 1:\n\nInput: s = "barfoothefoobarman", words = ["foo","bar"]\nOutput: [0,9]\nExplanation:\nThe substring starting at 0 is "barfoo". It is the concatenation of ["bar","foo"] which is a permutation of words.\nThe substring starting at 9 is "foobar". It is the concatenation of ["foo","bar"] which is a permutation of words.\n\nExample 2:\n\nInput: s = "wordgoodgoodgoodbestword", 

In [32]:
write_jsonl('leetcode-1046-0413-think-dpo-llama.jsonl', result)